In [2]:
%matplotlib notebook
import matplotlib.pyplot as plt

In [3]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from math import sqrt

from sklearn.preprocessing import MinMaxScaler
from catboost import CatBoostRegressor
from sklearn.linear_model import LinearRegression

from sklearn.preprocessing import OneHotEncoder
from scipy.stats.stats import pearsonr

from collections import Counter
import seaborn as sns
sns.set(style="darkgrid")

In [4]:
import xgboost as xgb
from sklearn.ensemble import GradientBoostingRegressor
from mlxtend.classifier import EnsembleVoteClassifier

from sklearn.ensemble import AdaBoostRegressor
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor

In [5]:
test_df = pd.read_csv("test_car0408.csv")
train_df = pd.read_csv("train_car0408.csv")

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (4,7,9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (4,7,8,9,18) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [192]:
train_df.head()

ID seller_type country_of_use scrapped_date postal_code  \
0   1     private         london    24/03/2016       66954   
1   3     private         london    17/03/2016       91074   
2   4     private         london    31/03/2016       60437   
3   5     private         london    04/04/2016       33775   
4   8     private         london    17/03/2016       27472   

                                            car_name   car_type  \
0                               A5_Sportback_2.7_Tdi      coupé   
1                                 GOLF_4_1_4__3TÜRER  small car   
2                     Skoda_Fabia_1.4_TDI_PD_Classic  small car   
3  BMW_316i___e36_Limousine___Bastlerfahrzeug__Ex...  limousine   
4  VW_Golf_4_5_tuerig_zu_verkaufen_mit_Anhaengerk...  small car   

  year_of_registration registration_month horse_power   mileage  gas_type  \
0                 2013                  5         190  201125.0    diesel   
1                 2003                  6          75  241350.0  gasoline   
2                 2010                  7          69  144810.0    diesel   
3                 1997                 10         102  241350.0  gasoline   
4                 2000                  0         101  241350.0       NaN   

    car_brand repair_status gear_type date_of_advert last_advert_online  \
0        audi           Yes   manuell     24/03/2016         07/04/2016   
1  volkswagen            No   manuell     17/03/2016         17/03/2016   
2       skoda            No   manuell     31/03/2016         06/04/2016   
3         bmw           Yes   manuell     04/04/2016         06/04/2016   
4  volkswagen           NaN   manuell     17/03/2016         31/03/2016   

   model naira_price  
0    NaN     6588000  
1   golf      540000  
2  fabia     1296000  
3    3er      234000  
4   golf      359640

In [ ]:
"90480" in train_df["postal_code"].tolis

In [194]:
train_df.shape

(224537, 19)

In [6]:
test_df.head()

ID seller_type country_of_use scrapped_date postal_code  \
0   2     private         london    14/03/2016       90480   
1   6     private         london    01/04/2016       67112   
2   7     private         london    04/04/2016       94505   
3  11     private         london    15/03/2016       37269   
4  12     private         london    21/03/2016       90762   

                               car_name       car_type year_of_registration  \
0        Jeep_Grand_Cherokee_"Overland"            NaN                 2006   
1           Peugeot_206_CC_110_Platinum    convertible                 2006   
2  Ford_C___Max_Titanium_1_0_L_EcoBoost            bus                 2016   
3     VW_Passat_Facelift_35i__"7Sitzer"  station wagon                 1997   
4        VW_PASSAT_1.9_TDI_131_PS_LEDER  station wagon                 2006   

   registration_month horse_power mileage  gas_type   car_brand repair_status  \
0                   8         163  201125    diesel        jeep           NaN   
1                   8         109  241350  gasoline     peugeot          nein   
2                   8         125   48270  gasoline        ford           NaN   
3                  11         115  241350  gasoline  volkswagen           NaN   
4                   2         131  241350       NaN  volkswagen          nein   

   gear_type date_of_advert last_advert_online    model  Unnamed: 18  
0  automatik     14/03/2016         05/04/2016    grand          NaN  
1    manuell     01/04/2016         05/04/2016  2_reihe          NaN  
2    manuell     04/04/2016         04/04/2016    c_max          NaN  
3    manuell     15/03/2016         01/04/2016   passat          NaN  
4    manuell     21/03/2016         23/03/2016   passat          NaN

# Replacing missing values with 0

In [6]:
zero_train = train_df.replace(np.nan, 0)
zero_test = test_df.replace(np.nan, 0)

# Data inputing

In [51]:
car_type_mode = 0# zero_test["car_type"].mode()
temp = np.asarray(zero_test["car_type"])
temp = np.where(temp == '125000', car_type_mode, temp)
temp = np.where(temp == '102', car_type_mode, temp)
temp = np.where(temp == 'test', car_type_mode, temp)
temp = np.where(temp == 'control', car_type_mode, temp)
temp = np.where(temp == 'privat', car_type_mode, temp)
zero_test["car_type"] = temp

car_brand_mode = 0# zero_test["car_brand"].mode()
temp = np.asarray(zero_test["car_brand"])
temp = np.where(temp == 'manuell', car_brand_mode, temp)
temp = np.where(temp == '150000', car_brand_mode, temp)
temp = np.where(temp == '90000', car_brand_mode, temp)
temp = np.where(temp == '0', car_brand_mode, temp)
temp = np.where(temp == '5000', car_brand_mode, temp)
temp = np.where(temp == '40000', car_brand_mode, temp)
temp = np.where(temp == '50000', car_brand_mode, temp)
temp = np.where(temp == '09/03/2016', car_brand_mode, temp)
zero_test["car_brand"] = temp

postal_code_mode = 0# zero_test["postal_code"].mode()
temp = np.asarray(zero_test["postal_code"])
temp = np.where(temp == 'Angebot', postal_code_mode, temp)
zero_test["postal_code"] = temp.astype(int)

registration_year_mode = 0# zero_test["year_of_registration"].mode()
temp = np.asarray(zero_test["year_of_registration"])
temp = np.where(temp == 'Angebot', registration_year_mode, temp)
temp = np.where(temp == 'andere', registration_year_mode, temp)
temp = np.where(temp == 'limousine', registration_year_mode, temp)
temp = np.where(temp == 'bus', registration_year_mode, temp)
zero_test["year_of_registration"] = temp.astype(int)

gear_type_mode = 0# zero_test["gear_type"].mode()
temp = np.asarray(zero_test["gear_type"])
temp = np.where(temp == 'diesel', gear_type_mode, temp)
temp = np.where(temp == 'lupo', gear_type_mode, temp)
temp = np.where(temp == 'vectra', gear_type_mode, temp)
temp = np.where(temp == 'benzin', gear_type_mode, temp)
temp = np.where(temp == 'hybrid', gear_type_mode, temp)
zero_test["gear_type"] = temp


horse_power_mode = 0# zero_test["horse_power"].mode()
temp = np.asarray(zero_test["horse_power"])
temp = np.where(temp == 'test', horse_power_mode, temp)
temp = np.where(temp == 'manuell', horse_power_mode, temp)
temp = np.where(temp == 'automatik', horse_power_mode, temp)
zero_test["horse_power"] = temp.astype(int)

model_mode = 0# zero_test["model"].mode()
temp = np.asarray(zero_test["model"])
temp = np.where(temp == '0', model_mode, temp)
zero_test["model"] = temp

scrapped_date_mode = 0# zero_test["scrapped_date"].mode()
temp = np.asarray(zero_test["scrapped_date"])
temp = np.where(temp == 'NaT', scrapped_date_mode, temp)
zero_test["scrapped_date"] = temp

advert_date_mode  = 0# zero_test["date_of_advert"].mode()
temp = np.asarray(zero_test["date_of_advert"])
temp = np.where(temp == 'volkswagen', advert_date_mode, temp)
temp = np.where(temp == 'toyota', advert_date_mode, temp)
temp = np.where(temp == 'renault', advert_date_mode, temp)
temp = np.where(temp == 'land_rover', advert_date_mode, temp)
temp = np.where(temp == 'mercedes_benz', advert_date_mode, temp)
temp = np.where(temp == 'ford', advert_date_mode, temp)
temp = np.where(temp == 'octavia', advert_date_mode, temp)
temp = np.where(temp == '150000', advert_date_mode, temp)
zero_test["date_of_advert"] = temp

last_advert_mode  = 0# zero_test["last_advert_online"].mode()
temp = np.asarray(zero_test["last_advert_online"])
temp = np.where(temp == '8', last_advert_mode, temp)
temp = np.where(temp == '4', last_advert_mode, temp)
temp = np.where(temp == 'nein', last_advert_mode, temp)
temp = np.where(temp == 'ja', last_advert_mode, temp)
zero_test["last_advert_online"] = temp

gas_type_mode = 0# zero_test["gas_type"].mode()
temp = np.asarray(zero_test["gas_type"])
temp = np.where(temp == '2002', gas_type_mode, temp)
temp = np.where(temp == '2000', gas_type_mode, temp)
temp = np.where(temp == 'golf', gas_type_mode, temp)
temp = np.where(temp == 'andere', gas_type_mode, temp)
temp = np.where(temp == 'clio', gas_type_mode, temp)
temp = np.where(temp == 'fiesta', gas_type_mode, temp)
temp = np.where(temp == 'manuell', gas_type_mode, temp)
temp = np.where(temp == 'c_klasse', gas_type_mode, temp)
temp = np.where(temp == 'a_klasse', gas_type_mode, temp)
temp = np.where(temp == 'defender', gas_type_mode, temp)
temp = np.where(temp == '19/03/2016 00:00', gas_type_mode, temp)
zero_test["gas_type"] = temp

repair_status_mode = 0# zero_train["repair_status"].mode()
temp = np.asarray(zero_test["repair_status"])
temp = np.where(temp == '51645', repair_status_mode, temp)
temp = np.where(temp == '10', repair_status_mode, temp)
temp = np.where(temp == '4', repair_status_mode, temp)
temp = np.where(temp == '6', repair_status_mode, temp)
temp = np.where(temp == '7', repair_status_mode, temp)
temp = np.where(temp == '15/03/2016', repair_status_mode, temp)
temp = np.where(temp == '75', repair_status_mode, temp)
temp = np.where(temp == '0', repair_status_mode, temp)
temp = np.where(temp == '4', repair_status_mode, temp)
temp = np.where(temp == '6', repair_status_mode, temp)
zero_test['repair_status'] = temp

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:24: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:29: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:30: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:31: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:32: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will p

In [52]:
# For train set:``

In [53]:
car_type_mode = 0# zero_train["car_type"].mode()
temp = np.asarray(zero_train["car_type"])
temp = np.where(temp == '125000', car_type_mode, temp)
temp = np.where(temp == '102', car_type_mode, temp)
temp = np.where(temp == 'test', car_type_mode, temp)
temp = np.where(temp == 'control', car_type_mode, temp)
zero_train["car_type"] = temp

car_brand_mode = 0# zero_train["car_type"].mode()
temp = np.asarray(zero_train["car_brand"])
temp = np.where(temp == '0', car_brand_mode, temp)
temp = np.where(temp == '150000', car_brand_mode, temp)
temp = np.where(temp == '5000', car_brand_mode, temp)
temp = np.where(temp == '40000', car_brand_mode, temp)
temp = np.where(temp == '50000', car_brand_mode, temp)
temp = np.where(temp == '09/03/2016', car_brand_mode, temp)
zero_train["car_brand"] = temp

postal_code_mode = 0# zero_train["postal_code"].mode()
temp = np.asarray(zero_train["postal_code"])
temp = np.where(temp == 'Angebot', postal_code_mode, temp)
zero_train["postal_code"] = temp.astype(int)

registration_year_mode = 0# zero_train["year_of_registration"].mode()
temp = np.asarray(zero_train["year_of_registration"])
temp = np.where(temp == 'Angebot', registration_year_mode, temp)
temp = np.where(temp == 'andere', registration_year_mode, temp)
temp = np.where(temp == 'limousine', registration_year_mode, temp)
temp = np.where(temp == 'bus', registration_year_mode, temp)
temp = np.where(temp == 'suv', registration_year_mode, temp)
temp = np.where(temp == 'kleinwagen', registration_year_mode, temp)
temp = np.where(temp == 'cabrio', registration_year_mode, temp)
temp = np.where(temp == 'coupe', registration_year_mode, temp)
zero_train["year_of_registration"] = temp.astype(int)

gear_type_mode = 0# zero_train["gear_type"].mode()
temp = np.asarray(zero_train["gear_type"])
temp = np.where(temp == 'diesel', gear_type_mode, temp)
temp = np.where(temp == 'lupo', gear_type_mode, temp)
temp = np.where(temp == 'vectra', gear_type_mode, temp)
temp = np.where(temp == 'benzin', gear_type_mode, temp)
temp = np.where(temp == 'hybrid', gear_type_mode, temp)
zero_train["gear_type"] = temp

horse_power_mode = 0# zero_train["horse_power"].mode()
temp = np.asarray(zero_train["horse_power"])
temp = np.where(temp == 'test', horse_power_mode, temp)
temp = np.where(temp == 'manuell', horse_power_mode, temp)
temp = np.where(temp == 'automatik', horse_power_mode, temp)
temp = np.where(temp == 'renault', horse_power_mode, temp)
temp = np.where(temp == 'skoda', horse_power_mode, temp)
zero_train["horse_power"] = temp.astype(int)

model_mode = 0# zero_train["model"].mode()
temp = np.asarray(zero_train["model"])
temp = np.where(temp == '0', model_mode, temp)
zero_train["model"] = temp

scrapped_date_mode = 0# zero_train["scrapped_date"].mode()
temp = np.asarray(zero_train["scrapped_date"])
temp = np.where(temp == 'NaT', scrapped_date_mode, temp)
zero_train["scrapped_date"] = temp

advert_date_mode  = 0# zero_train["date_of_advert"].mode()
temp = np.asarray(zero_train["date_of_advert"])
temp = np.where(temp == 'volkswagen', advert_date_mode, temp)
temp = np.where(temp == 'toyota', advert_date_mode, temp)
temp = np.where(temp == 'renault', advert_date_mode, temp)
temp = np.where(temp == 'land_rover', advert_date_mode, temp)
temp = np.where(temp == 'mercedes_benz', advert_date_mode, temp)
temp = np.where(temp == 'ford', advert_date_mode, temp)
temp = np.where(temp == 'octavia', advert_date_mode, temp)
zero_train["date_of_advert"] = temp

last_advert_mode  = 0# zero_train["last_advert_online"].mode()
temp = np.asarray(zero_train["last_advert_online"])
temp = np.where(temp == '8', last_advert_mode, temp)
temp = np.where(temp == '4', last_advert_mode, temp)
temp = np.where(temp == 'nein', last_advert_mode, temp)
temp = np.where(temp == 'ja', last_advert_mode, temp)
zero_train["last_advert_online"] = temp

gas_type_mode = 0# zero_train["gas_type"].mode()
temp = np.asarray(zero_train["gas_type"])
temp = np.where(temp == '2002', gas_type_mode, temp)
temp = np.where(temp == '2000', gas_type_mode, temp)
temp = np.where(temp == 'golf', gas_type_mode, temp)
temp = np.where(temp == 'andere', gas_type_mode, temp)
temp = np.where(temp == 'clio', gas_type_mode, temp)
temp = np.where(temp == 'fiesta', gas_type_mode, temp)
temp = np.where(temp == 'manuell', gas_type_mode, temp)
temp = np.where(temp == 'c_klasse', gas_type_mode, temp)
temp = np.where(temp == 'a_klasse', gas_type_mode, temp)
temp = np.where(temp == 'defender', gas_type_mode, temp)
temp = np.where(temp == '19/03/2016 00:00', gas_type_mode, temp)
zero_train["gas_type"] = temp

repair_status_mode = 0# zero_train["repair_status"].mode()
temp = np.asarray(zero_train["repair_status"])
temp = np.where(temp == '51645', repair_status_mode, temp)
temp = np.where(temp == '10', repair_status_mode, temp)
temp = np.where(temp == '4', repair_status_mode, temp)
temp = np.where(temp == '6', repair_status_mode, temp)
temp = np.where(temp == '7', repair_status_mode, temp)
temp = np.where(temp == '15/03/2016', repair_status_mode, temp)
temp = np.where(temp == '75', repair_status_mode, temp)
temp = np.where(temp == '0', repair_status_mode, temp)
temp = np.where(temp == '4', repair_status_mode, temp)
temp = np.where(temp == '6', repair_status_mode, temp)
zero_train['repair_status'] = temp

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:21: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:26: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:27: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:28: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:29: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will p

In [10]:
# Dealing with naira_price issue.
tmp_lst = []
for price in zero_train["naira_price"].tolist():
    try:
        tmp_lst.append(float(price))
    except Exception:
        print(price)

naira_price_mean = round(sum(tmp_lst)/len(tmp_lst))
print("naira_price_mean: ", naira_price_mean)

temp = np.asarray(zero_train["naira_price"])
temp = np.where(temp == '07/03/2016 00:00', naira_price_mean, temp)
temp = np.where(temp == '13/03/2016 00:00', naira_price_mean, temp)
temp = np.where(temp == '20/03/2016 00:00', naira_price_mean, temp)
temp = np.where(temp == '24/03/2016 00:00', naira_price_mean, temp)
temp = np.where(temp == '27/03/2016 00:00', naira_price_mean, temp)
temp = np.where(temp == '25/03/2016 00:00', naira_price_mean, temp)
temp = np.where(temp == '26/03/2016 00:00', naira_price_mean, temp)
zero_train["naira_price"] = temp.astype(float)

07/03/2016 00:00
13/03/2016 00:00
20/03/2016 00:00
24/03/2016 00:00
27/03/2016 00:00
25/03/2016 00:00
26/03/2016 00:00
naira_price_mean:  2262593


In [11]:
zero_train.head(3)

ID seller_type country_of_use scrapped_date  postal_code  \
0   1     private         london    24/03/2016        66954   
1   3     private         london    17/03/2016        91074   
2   4     private         london    31/03/2016        60437   

                         car_name   car_type  year_of_registration  \
0            A5_Sportback_2.7_Tdi      coupé                  2013   
1              GOLF_4_1_4__3TÜRER  small car                  2003   
2  Skoda_Fabia_1.4_TDI_PD_Classic  small car                  2010   

  registration_month  horse_power   mileage  gas_type   car_brand  \
0                  5          190  201125.0    diesel        audi   
1                  6           75  241350.0  gasoline  volkswagen   
2                  7           69  144810.0    diesel       skoda   

  repair_status gear_type date_of_advert last_advert_online  model  \
0           Yes   manuell     24/03/2016         07/04/2016      0   
1            No   manuell     17/03/2016         17/03/2016   golf   
2            No   manuell     31/03/2016         06/04/2016  fabia   

   naira_price  
0    6588000.0  
1     540000.0  
2    1296000.0

# Straight to ML model:

In [54]:
date_colums = ["scrapped_date", "date_of_advert", "last_advert_online" ]

train_columns = [ 'postal_code', 'year_of_registration', 'horse_power', 'mileage']

string_columns = ["car_type", "gas_type", "car_brand", "repair_status",
                  "gear_type", "model"]

In [92]:
train_copy = zero_train.copy()

In [93]:
#For label encoding to work... Replcaing int 0 with "a" - it would still be transformed to 0.
#Replacing 0 with the modes instead.

train_copy["car_type"] = train_copy["car_type"].replace([0], "a")#train_copy["car_type"].mode() )
train_copy["gas_type"] = train_copy["gas_type"].replace([0], "a")#train_copy["gas_type"].mode() )
train_copy["car_brand"] = train_copy["car_brand"].replace([0], "a")#train_copy["car_brand"].mode() )
train_copy["repair_status"] = train_copy["repair_status"].replace([0], "a")#train_copy["repair_status"].mode() )
train_copy["gear_type"] = train_copy["gear_type"].replace([0], "a")#train_copy["gear_type"].mode() )
train_copy["model"] = train_copy["model"].replace([0], "a")#train_copy["model"].mode() )

In [94]:
train_copy["car_brand"].unique()

array(['audi', 'volkswagen', 'skoda', 'bmw', 'mazda', 'nissan', 'renault',
       'ford', 'opel', 'mercedes_benz', 'honda', 'fiat', 'mini', 'smart',
       'hyundai', 'seat', 'subaru', 'volvo', 'mitsubishi', 'kia',
       'peugeot', 'suzuki', 'vauxhall', 'porsche', 'citroen', 'chevrolet',
       'sonstige_autos', 'dacia', 'daihatsu', 'alfa_romeo', 'toyota',
       'chrysler', 'daewoo', 'rover', 'jeep', 'saab', 'innoson',
       'land_rover', 'trabant', 'lotus', 'a'], dtype=object)

In [95]:
#Some models are in test_df but not in train_df
model_train =zero_train["model"].unique().tolist()
model_test =zero_test["model"].unique().tolist()
[i for i in model_test if i not in model_train]

['volkswagen', 'opel']

In [96]:
string_columns[:-1]

['car_type', 'gas_type', 'car_brand', 'repair_status', 'gear_type']

In [97]:
encoder_dict = {}
for column in string_columns[:-1]:
    encoder_dict[column] = LabelEncoder().fit(train_copy[column])

encoder_dict["model"] = LabelEncoder().fit(train_copy["model"].unique().tolist() + ['volkswagen', 'opel'])


In [98]:
# Transforming string columns:
for column in string_columns:
    train_copy[column] = encoder_dict[column].transform(train_copy[column])

In [99]:
train_copy[date_colums] = train_copy[date_colums].apply(pd.to_datetime)

# Convertung timestamps to UNIX float.

In [100]:
train_copy['scrapped_date'] = pd.to_datetime(train_copy['scrapped_date']).astype(int)/ 10**9
train_copy['date_of_advert'] = pd.to_datetime(train_copy['date_of_advert']).astype(int)/ 10**9
train_copy['last_advert_online'] = pd.to_datetime(train_copy['last_advert_online']).astype(int)/ 10**9

In [101]:
train_copy.head(2)

ID seller_type country_of_use  scrapped_date  postal_code  \
0   1     private         london   1.458778e+09        66954   
1   3     private         london   1.458173e+09        91074   

               car_name  car_type  year_of_registration registration_month  \
0  A5_Sportback_2.7_Tdi         3                  2013                  5   
1    GOLF_4_1_4__3TÜRER         6                  2003                  6   

   horse_power   mileage  gas_type  car_brand  repair_status  gear_type  \
0          190  201125.0         2          2              1          4   
1           75  241350.0         3         39              0          4   

   date_of_advert  last_advert_online  model  naira_price  
0    1.458778e+09        1.467590e+09     26    6588000.0  
1    1.458173e+09        1.458173e+09    119     540000.0

In [102]:
features_columns = train_columns + string_columns + date_colums

In [103]:
X_train, X_test, y_train, y_test = train_test_split( train_copy[features_columns], train_copy['naira_price'], test_size=0.3, random_state=42)


In [65]:
xgb_model = xgb.XGBRegressor().fit(X_train, y_train)
xgb_pred = xgb_model.predict(X_test)
metric_score = mean_squared_error(y_test, xgb_pred)
print("Metric Score: ", sqrt(metric_score) )

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


[20:07:36] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
Metric Score:  1561685.2202327289


In [146]:
# Tuned XGB Boost;#max_depth=5, min_child_weight=2
xgb_model = xgb.XGBRegressor(max_depth=10).fit(X_train, y_train)
xgb_pred = xgb_model.predict(X_test)
metric_score = mean_squared_error(y_test, xgb_pred)
print("Metric Score: ", sqrt(metric_score) )
#1297302.9541585222 with max_depth=10
#1280497.6948512164 with max_depth=9
#1316256.9889638135 with max_depth=11

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


[23:25:30] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
Metric Score:  1297315.6667542593


In [169]:
rf_model = RandomForestRegressor().fit(X_train, y_train)

rf_pred = rf_model.predict(X_test)
metric_score = mean_squared_error(y_test, rf_pred)
print("Metric Score: ", sqrt(metric_score) )

#Former(using mode) rf metric score: 1375914.0480555017
#Then Metric Score:  1367628.1329729143 with zero using 0.2

TypeError: __init__() got an unexpected keyword argument 'learning_rate'

In [ ]:
# RF with date_colums: Metric Score:  1404710.3184684245

In [171]:
gb_model = GradientBoostingRegressor(learning_rate=0.05).fit(X_train, y_train)

gb_pred = gb_model.predict(X_test)
metric_score = mean_squared_error(y_test, gb_pred)
print("Metric Score: ", sqrt(metric_score) )

#gb_model with date_colums> Metric Score:  1539673.6515541214

#1567117.6549353697 using 0.2

Metric Score:  1688327.8982801226


In [168]:
ada_model = AdaBoostRegressor(learning_rate=0.02).fit(X_train, y_train)

ada_pred = ada_model.predict(X_test)
metric_score = mean_squared_error(y_test, ada_pred)
print("Metric Score: ", sqrt(metric_score) )

#2200302.361275482 with learning_rate=0.05

Metric Score:  2195632.721555441


In [159]:
#Using CatBoost model with 1000 iterations.
cat_model1000 = CatBoostRegressor(iterations = 1000, depth=12).fit(X_train, y_train)

0:	learn: 3748236.1658143	total: 80ms	remaining: 1m 19s
1:	learn: 3665911.0229444	total: 142ms	remaining: 1m 11s
2:	learn: 3585561.3492481	total: 202ms	remaining: 1m 7s
3:	learn: 3508892.3514993	total: 268ms	remaining: 1m 6s
4:	learn: 3438139.8490370	total: 332ms	remaining: 1m 6s
5:	learn: 3366666.1413619	total: 394ms	remaining: 1m 5s
6:	learn: 3296430.3934670	total: 456ms	remaining: 1m 4s
7:	learn: 3229807.1958608	total: 519ms	remaining: 1m 4s
8:	learn: 3166470.6462506	total: 588ms	remaining: 1m 4s
9:	learn: 3102974.2750258	total: 656ms	remaining: 1m 4s
10:	learn: 3040068.2161591	total: 718ms	remaining: 1m 4s
11:	learn: 2979845.2499679	total: 784ms	remaining: 1m 4s
12:	learn: 2922850.9281958	total: 852ms	remaining: 1m 4s
13:	learn: 2867771.3882838	total: 920ms	remaining: 1m 4s
14:	learn: 2814501.9412759	total: 986ms	remaining: 1m 4s
15:	learn: 2764424.1484198	total: 1.05s	remaining: 1m 4s
16:	learn: 2715119.9261611	total: 1.12s	remaining: 1m 4s
17:	learn: 2668391.3413043	total: 1.19s	

147:	learn: 1269437.0684270	total: 9.62s	remaining: 55.4s
148:	learn: 1267650.8605414	total: 9.69s	remaining: 55.3s
149:	learn: 1266552.4579545	total: 9.75s	remaining: 55.3s
150:	learn: 1264875.7688530	total: 9.82s	remaining: 55.2s
151:	learn: 1263287.3089060	total: 9.88s	remaining: 55.1s
152:	learn: 1262171.8329374	total: 9.95s	remaining: 55.1s
153:	learn: 1260344.8955189	total: 10s	remaining: 55s
154:	learn: 1258995.8550890	total: 10.1s	remaining: 54.9s
155:	learn: 1257448.5671633	total: 10.1s	remaining: 54.9s
156:	learn: 1256212.9146121	total: 10.2s	remaining: 54.8s
157:	learn: 1254549.6409648	total: 10.3s	remaining: 54.7s
158:	learn: 1253083.1915064	total: 10.3s	remaining: 54.7s
159:	learn: 1251276.4444054	total: 10.4s	remaining: 54.6s
160:	learn: 1249356.9601297	total: 10.5s	remaining: 54.5s
161:	learn: 1247896.2787235	total: 10.5s	remaining: 54.5s
162:	learn: 1246410.1882259	total: 10.6s	remaining: 54.4s
163:	learn: 1245364.5199087	total: 10.7s	remaining: 54.3s
164:	learn: 124362

290:	learn: 1103521.0346047	total: 19s	remaining: 46.2s
291:	learn: 1102946.7428021	total: 19s	remaining: 46.1s
292:	learn: 1102163.6726594	total: 19.1s	remaining: 46.1s
293:	learn: 1101365.8910672	total: 19.2s	remaining: 46s
294:	learn: 1100336.5138953	total: 19.2s	remaining: 45.9s
295:	learn: 1099777.1469844	total: 19.3s	remaining: 45.9s
296:	learn: 1099001.3716523	total: 19.4s	remaining: 45.8s
297:	learn: 1098145.6568783	total: 19.4s	remaining: 45.7s
298:	learn: 1096967.7771675	total: 19.5s	remaining: 45.7s
299:	learn: 1095957.7526269	total: 19.6s	remaining: 45.6s
300:	learn: 1095275.9638271	total: 19.6s	remaining: 45.6s
301:	learn: 1094375.5364483	total: 19.7s	remaining: 45.5s
302:	learn: 1093451.6043822	total: 19.8s	remaining: 45.4s
303:	learn: 1092694.9573018	total: 19.8s	remaining: 45.4s
304:	learn: 1092126.4926836	total: 19.9s	remaining: 45.3s
305:	learn: 1091404.8400572	total: 20s	remaining: 45.3s
306:	learn: 1090626.9721504	total: 20s	remaining: 45.2s
307:	learn: 1089554.8071

434:	learn: 1004206.7341654	total: 28.5s	remaining: 37s
435:	learn: 1003801.9915089	total: 28.5s	remaining: 36.9s
436:	learn: 1002997.6223359	total: 28.6s	remaining: 36.9s
437:	learn: 1002568.3714149	total: 28.7s	remaining: 36.8s
438:	learn: 1002052.0087781	total: 28.7s	remaining: 36.7s
439:	learn: 1001602.3517523	total: 28.8s	remaining: 36.7s
440:	learn: 1001054.4813878	total: 28.9s	remaining: 36.6s
441:	learn: 1000257.6848140	total: 28.9s	remaining: 36.5s
442:	learn: 999703.8712277	total: 29s	remaining: 36.5s
443:	learn: 999234.8026124	total: 29.1s	remaining: 36.4s
444:	learn: 998486.4532461	total: 29.1s	remaining: 36.3s
445:	learn: 998066.0388433	total: 29.2s	remaining: 36.3s
446:	learn: 997497.0516649	total: 29.3s	remaining: 36.2s
447:	learn: 997116.3605385	total: 29.3s	remaining: 36.1s
448:	learn: 996546.8911598	total: 29.4s	remaining: 36.1s
449:	learn: 995890.3975134	total: 29.5s	remaining: 36s
450:	learn: 995438.3695669	total: 29.5s	remaining: 35.9s
451:	learn: 994735.8149550	to

580:	learn: 930925.3314213	total: 38s	remaining: 27.4s
581:	learn: 930385.0425259	total: 38.1s	remaining: 27.4s
582:	learn: 929786.9478046	total: 38.1s	remaining: 27.3s
583:	learn: 929342.0651068	total: 38.2s	remaining: 27.2s
584:	learn: 928931.3271321	total: 38.3s	remaining: 27.2s
585:	learn: 928399.9803926	total: 38.3s	remaining: 27.1s
586:	learn: 927546.2315410	total: 38.4s	remaining: 27s
587:	learn: 927177.4540697	total: 38.5s	remaining: 27s
588:	learn: 926914.2021345	total: 38.5s	remaining: 26.9s
589:	learn: 926521.5590165	total: 38.6s	remaining: 26.8s
590:	learn: 925687.0232760	total: 38.7s	remaining: 26.8s
591:	learn: 925276.1729121	total: 38.7s	remaining: 26.7s
592:	learn: 924880.7802266	total: 38.8s	remaining: 26.6s
593:	learn: 924367.1922484	total: 38.9s	remaining: 26.6s
594:	learn: 923980.7382438	total: 38.9s	remaining: 26.5s
595:	learn: 923644.9070220	total: 39s	remaining: 26.4s
596:	learn: 923121.8077928	total: 39.1s	remaining: 26.4s
597:	learn: 922871.5358038	total: 39.1s

727:	learn: 871480.2757744	total: 47.7s	remaining: 17.8s
728:	learn: 871048.5303891	total: 47.7s	remaining: 17.8s
729:	learn: 870759.6062974	total: 47.8s	remaining: 17.7s
730:	learn: 870532.3682401	total: 47.9s	remaining: 17.6s
731:	learn: 870124.5140663	total: 47.9s	remaining: 17.6s
732:	learn: 869767.2987336	total: 48s	remaining: 17.5s
733:	learn: 869358.3294086	total: 48.1s	remaining: 17.4s
734:	learn: 868974.3493208	total: 48.1s	remaining: 17.4s
735:	learn: 868596.2562530	total: 48.2s	remaining: 17.3s
736:	learn: 868116.1665002	total: 48.3s	remaining: 17.2s
737:	learn: 867778.8475110	total: 48.3s	remaining: 17.2s
738:	learn: 867332.3689971	total: 48.4s	remaining: 17.1s
739:	learn: 866983.2938153	total: 48.5s	remaining: 17s
740:	learn: 866733.4813306	total: 48.5s	remaining: 17s
741:	learn: 866256.3929676	total: 48.6s	remaining: 16.9s
742:	learn: 865830.0246650	total: 48.7s	remaining: 16.8s
743:	learn: 865555.5921768	total: 48.7s	remaining: 16.8s
744:	learn: 865097.1753488	total: 48.

872:	learn: 821720.1716740	total: 57.1s	remaining: 8.31s
873:	learn: 821535.8950768	total: 57.2s	remaining: 8.25s
874:	learn: 821190.9084321	total: 57.3s	remaining: 8.18s
875:	learn: 820899.6635001	total: 57.3s	remaining: 8.12s
876:	learn: 820625.4149513	total: 57.4s	remaining: 8.05s
877:	learn: 820302.1210033	total: 57.5s	remaining: 7.99s
878:	learn: 820009.3171393	total: 57.5s	remaining: 7.92s
879:	learn: 819730.2278342	total: 57.6s	remaining: 7.86s
880:	learn: 819454.3818864	total: 57.7s	remaining: 7.79s
881:	learn: 819162.1841382	total: 57.7s	remaining: 7.72s
882:	learn: 818884.2694893	total: 57.8s	remaining: 7.66s
883:	learn: 818279.7153293	total: 57.9s	remaining: 7.59s
884:	learn: 817958.9033232	total: 57.9s	remaining: 7.53s
885:	learn: 817726.5046330	total: 58s	remaining: 7.46s
886:	learn: 817498.7712124	total: 58.1s	remaining: 7.4s
887:	learn: 817129.6235535	total: 58.1s	remaining: 7.33s
888:	learn: 816746.1684716	total: 58.2s	remaining: 7.27s
889:	learn: 816254.0099817	total: 

In [160]:
cat_pred = cat_model1000.predict(X_test)
metric_score = mean_squared_error(y_test, cat_pred)
print("Metric Score: ", sqrt(metric_score) )

#cat1000 with date_colums: 1327494.7276910432
#1343203.0480951972 using 0.2

#1318130.3899717003 with iterations = 1000, depth=8
#1298914.5673787498 with iterations = 1000, depth=10
#1308000.3752558734 with iterations = 1000, depth=12

Metric Score:  1308000.3752558734


In [35]:
#Using CatBoost model with X iterations.
cat_modelX000 = CatBoostRegressor(iterations = 5000).fit(X_train, y_train)

0:	learn: 3749556.4376556	total: 19.3ms	remaining: 1m 36s
1:	learn: 3672822.6283858	total: 38.6ms	remaining: 1m 36s
2:	learn: 3598975.7770867	total: 57.6ms	remaining: 1m 35s
3:	learn: 3526948.0141068	total: 76.6ms	remaining: 1m 35s
4:	learn: 3457717.4409493	total: 94.9ms	remaining: 1m 34s
5:	learn: 3391203.2383097	total: 114ms	remaining: 1m 35s
6:	learn: 3327559.7009184	total: 133ms	remaining: 1m 34s
7:	learn: 3265238.4194365	total: 151ms	remaining: 1m 34s
8:	learn: 3205832.1820827	total: 170ms	remaining: 1m 34s
9:	learn: 3148949.3149051	total: 189ms	remaining: 1m 34s
10:	learn: 3093675.6288753	total: 207ms	remaining: 1m 34s
11:	learn: 3040689.3276913	total: 227ms	remaining: 1m 34s
12:	learn: 2989932.2992806	total: 246ms	remaining: 1m 34s
13:	learn: 2940434.9580970	total: 265ms	remaining: 1m 34s
14:	learn: 2892736.2705239	total: 284ms	remaining: 1m 34s
15:	learn: 2846471.9629185	total: 303ms	remaining: 1m 34s
16:	learn: 2803221.2137806	total: 322ms	remaining: 1m 34s
17:	learn: 2761518.

143:	learn: 1563053.9154251	total: 2.73s	remaining: 1m 31s
144:	learn: 1561770.3392414	total: 2.75s	remaining: 1m 31s
145:	learn: 1560388.9388842	total: 2.77s	remaining: 1m 31s
146:	learn: 1559390.1882190	total: 2.78s	remaining: 1m 31s
147:	learn: 1557706.3732264	total: 2.8s	remaining: 1m 31s
148:	learn: 1554639.7510906	total: 2.82s	remaining: 1m 31s
149:	learn: 1553104.8576768	total: 2.83s	remaining: 1m 31s
150:	learn: 1552034.8370725	total: 2.85s	remaining: 1m 31s
151:	learn: 1550386.6228925	total: 2.87s	remaining: 1m 31s
152:	learn: 1549632.6912328	total: 2.89s	remaining: 1m 31s
153:	learn: 1546808.9908914	total: 2.91s	remaining: 1m 31s
154:	learn: 1544532.5431153	total: 2.93s	remaining: 1m 31s
155:	learn: 1543000.4397180	total: 2.95s	remaining: 1m 31s
156:	learn: 1541631.3018672	total: 2.97s	remaining: 1m 31s
157:	learn: 1540849.5967844	total: 2.98s	remaining: 1m 31s
158:	learn: 1539441.0317981	total: 3s	remaining: 1m 31s
159:	learn: 1538076.3198686	total: 3.02s	remaining: 1m 31s
1

289:	learn: 1418548.4985443	total: 5.42s	remaining: 1m 28s
290:	learn: 1418401.4750671	total: 5.44s	remaining: 1m 28s
291:	learn: 1418221.5763965	total: 5.46s	remaining: 1m 28s
292:	learn: 1417606.4144847	total: 5.48s	remaining: 1m 27s
293:	learn: 1416666.5231650	total: 5.49s	remaining: 1m 27s
294:	learn: 1416496.3264108	total: 5.51s	remaining: 1m 27s
295:	learn: 1416113.4494328	total: 5.53s	remaining: 1m 27s
296:	learn: 1414558.8504542	total: 5.55s	remaining: 1m 27s
297:	learn: 1413905.1664084	total: 5.57s	remaining: 1m 27s
298:	learn: 1413344.0339365	total: 5.58s	remaining: 1m 27s
299:	learn: 1413094.7772618	total: 5.6s	remaining: 1m 27s
300:	learn: 1412239.8266454	total: 5.62s	remaining: 1m 27s
301:	learn: 1411890.9340425	total: 5.64s	remaining: 1m 27s
302:	learn: 1411378.8370223	total: 5.66s	remaining: 1m 27s
303:	learn: 1410734.5947664	total: 5.68s	remaining: 1m 27s
304:	learn: 1409995.6842033	total: 5.7s	remaining: 1m 27s
305:	learn: 1409411.1622035	total: 5.72s	remaining: 1m 27s

436:	learn: 1344240.1923315	total: 8.13s	remaining: 1m 24s
437:	learn: 1343772.2665754	total: 8.15s	remaining: 1m 24s
438:	learn: 1343237.7544167	total: 8.17s	remaining: 1m 24s
439:	learn: 1342956.2369327	total: 8.19s	remaining: 1m 24s
440:	learn: 1342795.4085809	total: 8.21s	remaining: 1m 24s
441:	learn: 1342397.0765601	total: 8.22s	remaining: 1m 24s
442:	learn: 1342126.3391981	total: 8.24s	remaining: 1m 24s
443:	learn: 1341950.2630912	total: 8.26s	remaining: 1m 24s
444:	learn: 1341722.7657511	total: 8.28s	remaining: 1m 24s
445:	learn: 1341134.6749063	total: 8.29s	remaining: 1m 24s
446:	learn: 1340906.8595832	total: 8.31s	remaining: 1m 24s
447:	learn: 1340611.8829692	total: 8.33s	remaining: 1m 24s
448:	learn: 1340175.6867631	total: 8.35s	remaining: 1m 24s
449:	learn: 1339614.1763929	total: 8.37s	remaining: 1m 24s
450:	learn: 1339357.4794035	total: 8.39s	remaining: 1m 24s
451:	learn: 1339027.1420555	total: 8.4s	remaining: 1m 24s
452:	learn: 1338426.5213867	total: 8.43s	remaining: 1m 24

583:	learn: 1290818.9812009	total: 10.8s	remaining: 1m 21s
584:	learn: 1290024.6800439	total: 10.9s	remaining: 1m 21s
585:	learn: 1289683.4640355	total: 10.9s	remaining: 1m 21s
586:	learn: 1289311.8879387	total: 10.9s	remaining: 1m 21s
587:	learn: 1288911.0200175	total: 10.9s	remaining: 1m 21s
588:	learn: 1288529.1342686	total: 10.9s	remaining: 1m 21s
589:	learn: 1287968.6872814	total: 10.9s	remaining: 1m 21s
590:	learn: 1287689.2702192	total: 11s	remaining: 1m 21s
591:	learn: 1287125.0966942	total: 11s	remaining: 1m 21s
592:	learn: 1286897.6543996	total: 11s	remaining: 1m 21s
593:	learn: 1286312.4154747	total: 11s	remaining: 1m 21s
594:	learn: 1286225.0029289	total: 11s	remaining: 1m 21s
595:	learn: 1285860.7490192	total: 11.1s	remaining: 1m 21s
596:	learn: 1285555.1275226	total: 11.1s	remaining: 1m 21s
597:	learn: 1285308.2294886	total: 11.1s	remaining: 1m 21s
598:	learn: 1284901.1296321	total: 11.1s	remaining: 1m 21s
599:	learn: 1284687.6749219	total: 11.1s	remaining: 1m 21s
600:	le

...

4358:	learn: 930957.0661390	total: 1m 20s	remaining: 11.8s
4359:	learn: 930901.4102943	total: 1m 20s	remaining: 11.8s
4360:	learn: 930872.7493575	total: 1m 20s	remaining: 11.8s
4361:	learn: 930849.7021863	total: 1m 20s	remaining: 11.7s
4362:	learn: 930814.5379472	total: 1m 20s	remaining: 11.7s
4363:	learn: 930764.9951544	total: 1m 20s	remaining: 11.7s
4364:	learn: 930742.7181631	total: 1m 20s	remaining: 11.7s
4365:	learn: 930708.3169879	total: 1m 20s	remaining: 11.7s
4366:	learn: 930635.7858862	total: 1m 20s	remaining: 11.7s
4367:	learn: 930571.0154222	total: 1m 20s	remaining: 11.6s
4368:	learn: 930520.2733659	total: 1m 20s	remaining: 11.6s
4369:	learn: 930405.2390229	total: 1m 20s	remaining: 11.6s
4370:	learn: 930370.8776698	total: 1m 20s	remaining: 11.6s
4371:	learn: 930296.8241769	total: 1m 20s	remaining: 11.6s
4372:	learn: 930269.0989025	total: 1m 20s	remaining: 11.5s
4373:	learn: 930233.7639540	total: 1m 20s	remaining: 11.5s
4374:	learn: 930207.4555210	total: 1m 20s	remaining: 11.

4509:	learn: 924277.7875642	total: 1m 22s	remaining: 9.02s
4510:	learn: 924252.7267434	total: 1m 23s	remaining: 9s
4511:	learn: 924228.8445059	total: 1m 23s	remaining: 8.98s
4512:	learn: 924210.9157660	total: 1m 23s	remaining: 8.96s
4513:	learn: 924192.6964951	total: 1m 23s	remaining: 8.94s
4514:	learn: 924159.8966490	total: 1m 23s	remaining: 8.93s
4515:	learn: 924033.2705502	total: 1m 23s	remaining: 8.91s
4516:	learn: 923981.8290566	total: 1m 23s	remaining: 8.89s
4517:	learn: 923954.0236501	total: 1m 23s	remaining: 8.87s
4518:	learn: 923932.9079937	total: 1m 23s	remaining: 8.85s
4519:	learn: 923900.8241660	total: 1m 23s	remaining: 8.83s
4520:	learn: 923880.8552073	total: 1m 23s	remaining: 8.81s
4521:	learn: 923806.0225776	total: 1m 23s	remaining: 8.79s
4522:	learn: 923722.4747627	total: 1m 23s	remaining: 8.78s
4523:	learn: 923695.8853138	total: 1m 23s	remaining: 8.76s
4524:	learn: 923659.6387203	total: 1m 23s	remaining: 8.74s
4525:	learn: 923599.3432537	total: 1m 23s	remaining: 8.72s


4654:	learn: 918728.6463521	total: 1m 25s	remaining: 6.35s
4655:	learn: 918690.5488228	total: 1m 25s	remaining: 6.33s
4656:	learn: 918639.7396083	total: 1m 25s	remaining: 6.31s
4657:	learn: 918622.6125106	total: 1m 25s	remaining: 6.29s
4658:	learn: 918591.1440693	total: 1m 25s	remaining: 6.28s
4659:	learn: 918529.3838038	total: 1m 25s	remaining: 6.26s
4660:	learn: 918473.5985033	total: 1m 25s	remaining: 6.24s
4661:	learn: 918339.1203222	total: 1m 25s	remaining: 6.22s
4662:	learn: 918279.3846590	total: 1m 25s	remaining: 6.2s
4663:	learn: 918226.7073906	total: 1m 25s	remaining: 6.18s
4664:	learn: 918188.1868016	total: 1m 25s	remaining: 6.17s
4665:	learn: 918175.9018820	total: 1m 25s	remaining: 6.15s
4666:	learn: 918150.4384360	total: 1m 25s	remaining: 6.13s
4667:	learn: 918136.2957696	total: 1m 25s	remaining: 6.11s
4668:	learn: 918097.5017071	total: 1m 25s	remaining: 6.09s
4669:	learn: 918016.4522957	total: 1m 25s	remaining: 6.07s
4670:	learn: 917955.7394038	total: 1m 25s	remaining: 6.05

4803:	learn: 912514.3343794	total: 1m 28s	remaining: 3.61s
4804:	learn: 912493.2512402	total: 1m 28s	remaining: 3.59s
4805:	learn: 912479.4272400	total: 1m 28s	remaining: 3.57s
4806:	learn: 912455.7194702	total: 1m 28s	remaining: 3.55s
4807:	learn: 912438.0140272	total: 1m 28s	remaining: 3.53s
4808:	learn: 912385.3616439	total: 1m 28s	remaining: 3.51s
4809:	learn: 912338.3514718	total: 1m 28s	remaining: 3.5s
4810:	learn: 912315.9488184	total: 1m 28s	remaining: 3.48s
4811:	learn: 912277.4823195	total: 1m 28s	remaining: 3.46s
4812:	learn: 912240.3429736	total: 1m 28s	remaining: 3.44s
4813:	learn: 912189.3157927	total: 1m 28s	remaining: 3.42s
4814:	learn: 912154.2437812	total: 1m 28s	remaining: 3.4s
4815:	learn: 912059.7634878	total: 1m 28s	remaining: 3.38s
4816:	learn: 912021.8743212	total: 1m 28s	remaining: 3.37s
4817:	learn: 911995.0482173	total: 1m 28s	remaining: 3.35s
4818:	learn: 911971.8554346	total: 1m 28s	remaining: 3.33s
4819:	learn: 911938.1854161	total: 1m 28s	remaining: 3.31s

4953:	learn: 907258.9843249	total: 1m 31s	remaining: 846ms
4954:	learn: 907244.9106225	total: 1m 31s	remaining: 828ms
4955:	learn: 907216.1354478	total: 1m 31s	remaining: 810ms
4956:	learn: 907200.4151942	total: 1m 31s	remaining: 791ms
4957:	learn: 907176.5526981	total: 1m 31s	remaining: 773ms
4958:	learn: 907136.2500104	total: 1m 31s	remaining: 754ms
4959:	learn: 907090.8801645	total: 1m 31s	remaining: 736ms
4960:	learn: 907060.8948171	total: 1m 31s	remaining: 718ms
4961:	learn: 907025.8929612	total: 1m 31s	remaining: 699ms
4962:	learn: 906991.7268593	total: 1m 31s	remaining: 681ms
4963:	learn: 906969.0425921	total: 1m 31s	remaining: 662ms
4964:	learn: 906919.8843675	total: 1m 31s	remaining: 644ms
4965:	learn: 906873.7326985	total: 1m 31s	remaining: 626ms
4966:	learn: 906843.2738854	total: 1m 31s	remaining: 607ms
4967:	learn: 906813.6442247	total: 1m 31s	remaining: 589ms
4968:	learn: 906782.7616645	total: 1m 31s	remaining: 570ms
4969:	learn: 906767.3785042	total: 1m 31s	remaining: 552

In [36]:
cat_pred = cat_modelX000.predict(X_test)
metric_score = mean_squared_error(y_test, cat_pred)
print("Metric Score: ", sqrt(metric_score) )
#Fromer score using mode> Metric Score:  1258994.1110511764

Metric Score:  1273145.884672903


In [37]:
cat_modelX000 = CatBoostRegressor(iterations = 5000).fit(train_copy[features_columns], train_copy["naira_price"])

0:	learn: 3749955.3845497	total: 30.9ms	remaining: 2m 34s
1:	learn: 3672849.4079857	total: 54.6ms	remaining: 2m 16s
2:	learn: 3598006.4786502	total: 77.6ms	remaining: 2m 9s
3:	learn: 3526188.4172321	total: 101ms	remaining: 2m 6s
4:	learn: 3455911.6384628	total: 124ms	remaining: 2m 4s
5:	learn: 3389156.4723908	total: 148ms	remaining: 2m 3s
6:	learn: 3324973.2537140	total: 172ms	remaining: 2m 2s
7:	learn: 3263307.0957264	total: 194ms	remaining: 2m 1s
8:	learn: 3203686.4631752	total: 218ms	remaining: 2m
9:	learn: 3145546.7497214	total: 242ms	remaining: 2m
10:	learn: 3089899.8666054	total: 265ms	remaining: 2m
11:	learn: 3036778.4636410	total: 288ms	remaining: 1m 59s
12:	learn: 2985715.3719153	total: 312ms	remaining: 1m 59s
13:	learn: 2936641.7659059	total: 336ms	remaining: 1m 59s
14:	learn: 2889069.2659479	total: 358ms	remaining: 1m 59s
15:	learn: 2842291.6623510	total: 382ms	remaining: 1m 59s
16:	learn: 2797740.4233600	total: 407ms	remaining: 1m 59s
17:	learn: 2754811.2689629	total: 428ms

145:	learn: 1557022.1285062	total: 3.42s	remaining: 1m 53s
146:	learn: 1554400.2505406	total: 3.44s	remaining: 1m 53s
147:	learn: 1552904.0384603	total: 3.47s	remaining: 1m 53s
148:	learn: 1551375.3056842	total: 3.49s	remaining: 1m 53s
149:	learn: 1550007.2542432	total: 3.52s	remaining: 1m 54s
150:	learn: 1549093.0058219	total: 3.55s	remaining: 1m 53s
151:	learn: 1547845.9686906	total: 3.57s	remaining: 1m 53s
152:	learn: 1546412.4564167	total: 3.6s	remaining: 1m 53s
153:	learn: 1544918.8564853	total: 3.62s	remaining: 1m 53s
154:	learn: 1543097.6036116	total: 3.64s	remaining: 1m 53s
155:	learn: 1541914.2754600	total: 3.67s	remaining: 1m 53s
156:	learn: 1540349.3832293	total: 3.69s	remaining: 1m 53s
157:	learn: 1539009.7163758	total: 3.71s	remaining: 1m 53s
158:	learn: 1537532.5976073	total: 3.73s	remaining: 1m 53s
159:	learn: 1536244.0509311	total: 3.76s	remaining: 1m 53s
160:	learn: 1534513.0376760	total: 3.78s	remaining: 1m 53s
161:	learn: 1533698.5588876	total: 3.81s	remaining: 1m 53

289:	learn: 1418760.0195828	total: 6.74s	remaining: 1m 49s
290:	learn: 1418175.8727632	total: 6.76s	remaining: 1m 49s
291:	learn: 1416691.5995632	total: 6.78s	remaining: 1m 49s
292:	learn: 1416171.4421049	total: 6.81s	remaining: 1m 49s
293:	learn: 1415351.7142227	total: 6.83s	remaining: 1m 49s
294:	learn: 1414816.5314966	total: 6.85s	remaining: 1m 49s
295:	learn: 1413978.5331240	total: 6.88s	remaining: 1m 49s
296:	learn: 1413318.9916687	total: 6.9s	remaining: 1m 49s
297:	learn: 1412844.7922073	total: 6.92s	remaining: 1m 49s
298:	learn: 1412391.1914584	total: 6.94s	remaining: 1m 49s
299:	learn: 1411451.4727710	total: 6.97s	remaining: 1m 49s
300:	learn: 1411022.8301859	total: 6.99s	remaining: 1m 49s
301:	learn: 1409449.5647022	total: 7.01s	remaining: 1m 49s
302:	learn: 1408245.1669842	total: 7.03s	remaining: 1m 49s
303:	learn: 1407531.6037550	total: 7.06s	remaining: 1m 49s
304:	learn: 1406910.5857897	total: 7.08s	remaining: 1m 49s
305:	learn: 1406343.8427043	total: 7.1s	remaining: 1m 48s

434:	learn: 1343472.5293377	total: 10.1s	remaining: 1m 45s
435:	learn: 1343154.6483739	total: 10.1s	remaining: 1m 45s
436:	learn: 1342714.0308382	total: 10.1s	remaining: 1m 45s
437:	learn: 1342337.3985751	total: 10.1s	remaining: 1m 45s
438:	learn: 1341939.1039027	total: 10.1s	remaining: 1m 45s
439:	learn: 1341589.7758991	total: 10.2s	remaining: 1m 45s
440:	learn: 1340944.6519290	total: 10.2s	remaining: 1m 45s
441:	learn: 1340355.8858626	total: 10.2s	remaining: 1m 45s
442:	learn: 1340081.4301937	total: 10.2s	remaining: 1m 45s
443:	learn: 1339884.8759192	total: 10.3s	remaining: 1m 45s
444:	learn: 1339691.8803371	total: 10.3s	remaining: 1m 45s
445:	learn: 1339569.6394832	total: 10.3s	remaining: 1m 45s
446:	learn: 1339066.9437530	total: 10.3s	remaining: 1m 45s
447:	learn: 1338586.1679151	total: 10.4s	remaining: 1m 45s
448:	learn: 1338381.5645423	total: 10.4s	remaining: 1m 45s
449:	learn: 1338019.8169198	total: 10.4s	remaining: 1m 45s
450:	learn: 1337562.0501313	total: 10.4s	remaining: 1m 4

580:	learn: 1292921.2494415	total: 13.4s	remaining: 1m 41s
581:	learn: 1292694.3621034	total: 13.4s	remaining: 1m 41s
582:	learn: 1292422.1143366	total: 13.4s	remaining: 1m 41s
583:	learn: 1292137.9371169	total: 13.5s	remaining: 1m 41s
584:	learn: 1291988.4231521	total: 13.5s	remaining: 1m 41s
585:	learn: 1291320.9845506	total: 13.5s	remaining: 1m 41s
586:	learn: 1290647.7123187	total: 13.5s	remaining: 1m 41s
587:	learn: 1290245.4797631	total: 13.6s	remaining: 1m 41s
588:	learn: 1290045.9599391	total: 13.6s	remaining: 1m 41s
589:	learn: 1289612.8777125	total: 13.6s	remaining: 1m 41s
590:	learn: 1289503.1475034	total: 13.6s	remaining: 1m 41s
591:	learn: 1289203.6961259	total: 13.6s	remaining: 1m 41s
592:	learn: 1288897.1451448	total: 13.7s	remaining: 1m 41s
593:	learn: 1288423.4899188	total: 13.7s	remaining: 1m 41s
594:	learn: 1288177.4765993	total: 13.7s	remaining: 1m 41s
595:	learn: 1287928.6078940	total: 13.7s	remaining: 1m 41s
596:	learn: 1287702.1791391	total: 13.8s	remaining: 1m 4

...

4304:	learn: 970575.8803801	total: 1m 38s	remaining: 15.8s
4305:	learn: 970562.1398057	total: 1m 38s	remaining: 15.8s
4306:	learn: 970534.7271007	total: 1m 38s	remaining: 15.8s
4307:	learn: 970457.5913558	total: 1m 38s	remaining: 15.8s
4308:	learn: 970443.0376058	total: 1m 38s	remaining: 15.8s
4309:	learn: 970434.0932974	total: 1m 38s	remaining: 15.7s
4310:	learn: 970412.3842332	total: 1m 38s	remaining: 15.7s
4311:	learn: 970283.7581453	total: 1m 38s	remaining: 15.7s
4312:	learn: 970243.0846360	total: 1m 38s	remaining: 15.7s
4313:	learn: 970197.0156450	total: 1m 38s	remaining: 15.6s
4314:	learn: 970167.3374334	total: 1m 38s	remaining: 15.6s
4315:	learn: 970141.3878448	total: 1m 38s	remaining: 15.6s
4316:	learn: 970050.2923864	total: 1m 38s	remaining: 15.6s
4317:	learn: 970001.7561634	total: 1m 38s	remaining: 15.5s
4318:	learn: 969966.3970350	total: 1m 38s	remaining: 15.5s
4319:	learn: 969924.5548199	total: 1m 38s	remaining: 15.5s
4320:	learn: 969906.8603656	total: 1m 38s	remaining: 15.

4448:	learn: 964570.8564213	total: 1m 41s	remaining: 12.6s
4449:	learn: 964535.6893108	total: 1m 41s	remaining: 12.5s
4450:	learn: 964514.7073107	total: 1m 41s	remaining: 12.5s
4451:	learn: 964469.0131443	total: 1m 41s	remaining: 12.5s
4452:	learn: 964439.5396399	total: 1m 41s	remaining: 12.5s
4453:	learn: 964365.3806558	total: 1m 41s	remaining: 12.4s
4454:	learn: 964350.8520470	total: 1m 41s	remaining: 12.4s
4455:	learn: 964303.7948121	total: 1m 41s	remaining: 12.4s
4456:	learn: 964263.6757973	total: 1m 41s	remaining: 12.4s
4457:	learn: 964234.9538171	total: 1m 41s	remaining: 12.4s
4458:	learn: 964193.4770198	total: 1m 41s	remaining: 12.3s
4459:	learn: 964139.7658803	total: 1m 41s	remaining: 12.3s
4460:	learn: 964110.6316161	total: 1m 41s	remaining: 12.3s
4461:	learn: 964090.8483227	total: 1m 41s	remaining: 12.3s
4462:	learn: 964045.5737487	total: 1m 41s	remaining: 12.2s
4463:	learn: 964021.4832107	total: 1m 41s	remaining: 12.2s
4464:	learn: 964005.5426313	total: 1m 41s	remaining: 12.

4596:	learn: 958966.0819845	total: 1m 44s	remaining: 9.18s
4597:	learn: 958928.1704015	total: 1m 44s	remaining: 9.16s
4598:	learn: 958910.6622367	total: 1m 44s	remaining: 9.14s
4599:	learn: 958884.6290415	total: 1m 44s	remaining: 9.12s
4600:	learn: 958843.4645271	total: 1m 44s	remaining: 9.09s
4601:	learn: 958824.6865186	total: 1m 44s	remaining: 9.07s
4602:	learn: 958771.3028594	total: 1m 44s	remaining: 9.05s
4603:	learn: 958718.9864390	total: 1m 44s	remaining: 9.02s
4604:	learn: 958678.0041492	total: 1m 44s	remaining: 9s
4605:	learn: 958635.2950363	total: 1m 44s	remaining: 8.98s
4606:	learn: 958591.1676653	total: 1m 44s	remaining: 8.96s
4607:	learn: 958562.4741652	total: 1m 45s	remaining: 8.93s
4608:	learn: 958538.9982189	total: 1m 45s	remaining: 8.91s
4609:	learn: 958498.7942289	total: 1m 45s	remaining: 8.89s
4610:	learn: 958469.7031264	total: 1m 45s	remaining: 8.86s
4611:	learn: 958445.6747733	total: 1m 45s	remaining: 8.84s
4612:	learn: 958413.0756898	total: 1m 45s	remaining: 8.82s


4741:	learn: 953406.3653102	total: 1m 48s	remaining: 5.88s
4742:	learn: 953379.8125230	total: 1m 48s	remaining: 5.86s
4743:	learn: 953329.6884437	total: 1m 48s	remaining: 5.83s
4744:	learn: 953296.5431435	total: 1m 48s	remaining: 5.81s
4745:	learn: 953267.9083944	total: 1m 48s	remaining: 5.79s
4746:	learn: 953232.5381253	total: 1m 48s	remaining: 5.77s
4747:	learn: 953203.8029271	total: 1m 48s	remaining: 5.74s
4748:	learn: 953151.1027716	total: 1m 48s	remaining: 5.72s
4749:	learn: 953129.6037172	total: 1m 48s	remaining: 5.7s
4750:	learn: 953096.8172250	total: 1m 48s	remaining: 5.67s
4751:	learn: 953075.9841164	total: 1m 48s	remaining: 5.65s
4752:	learn: 953039.0271834	total: 1m 48s	remaining: 5.63s
4753:	learn: 952989.2259954	total: 1m 48s	remaining: 5.61s
4754:	learn: 952960.4602708	total: 1m 48s	remaining: 5.58s
4755:	learn: 952907.6929078	total: 1m 48s	remaining: 5.56s
4756:	learn: 952858.9084108	total: 1m 48s	remaining: 5.54s
4757:	learn: 952825.7714080	total: 1m 48s	remaining: 5.52

4885:	learn: 948565.7043400	total: 1m 51s	remaining: 2.6s
4886:	learn: 948522.9118679	total: 1m 51s	remaining: 2.58s
4887:	learn: 948427.8076661	total: 1m 51s	remaining: 2.55s
4888:	learn: 948401.6129539	total: 1m 51s	remaining: 2.53s
4889:	learn: 948375.0015809	total: 1m 51s	remaining: 2.51s
4890:	learn: 948340.7800921	total: 1m 51s	remaining: 2.48s
4891:	learn: 948295.9864897	total: 1m 51s	remaining: 2.46s
4892:	learn: 948254.3796129	total: 1m 51s	remaining: 2.44s
4893:	learn: 948225.2364971	total: 1m 51s	remaining: 2.42s
4894:	learn: 948157.0398279	total: 1m 51s	remaining: 2.39s
4895:	learn: 948123.8531248	total: 1m 51s	remaining: 2.37s
4896:	learn: 948082.6737383	total: 1m 51s	remaining: 2.35s
4897:	learn: 948035.2398881	total: 1m 51s	remaining: 2.33s
4898:	learn: 948027.2840462	total: 1m 51s	remaining: 2.3s
4899:	learn: 947966.6860215	total: 1m 51s	remaining: 2.28s
4900:	learn: 947954.2500658	total: 1m 51s	remaining: 2.26s
4901:	learn: 947901.6434247	total: 1m 51s	remaining: 2.23s

In [137]:
cat_model10000 = CatBoostRegressor(iterations = 10000).fit(train_copy[features_columns], train_copy["naira_price"])


0:	learn: 3749797.0492992	total: 29.3ms	remaining: 4m 53s
1:	learn: 3672608.9735922	total: 52.5ms	remaining: 4m 22s
2:	learn: 3597486.4017296	total: 75.8ms	remaining: 4m 12s
3:	learn: 3525744.5189320	total: 101ms	remaining: 4m 11s
4:	learn: 3455406.8642599	total: 124ms	remaining: 4m 8s
5:	learn: 3388086.1671816	total: 148ms	remaining: 4m 6s
6:	learn: 3324434.9159011	total: 171ms	remaining: 4m 3s
7:	learn: 3262238.5447145	total: 194ms	remaining: 4m 1s
8:	learn: 3202273.7923378	total: 217ms	remaining: 4m
9:	learn: 3144501.7444038	total: 243ms	remaining: 4m 2s
10:	learn: 3088553.6554168	total: 266ms	remaining: 4m 1s
11:	learn: 3034854.1488539	total: 290ms	remaining: 4m 1s
12:	learn: 2982923.5069686	total: 314ms	remaining: 4m 1s
13:	learn: 2933189.9104814	total: 338ms	remaining: 4m
14:	learn: 2885284.5338898	total: 362ms	remaining: 4m
15:	learn: 2839680.2735827	total: 386ms	remaining: 4m
16:	learn: 2794905.9434648	total: 409ms	remaining: 3m 59s
17:	learn: 2752166.0564134	total: 430ms	remai

144:	learn: 1560238.0275044	total: 3.17s	remaining: 3m 35s
145:	learn: 1558921.6316960	total: 3.19s	remaining: 3m 35s
146:	learn: 1557247.7901959	total: 3.21s	remaining: 3m 35s
147:	learn: 1555801.1770276	total: 3.23s	remaining: 3m 35s
148:	learn: 1554826.2940501	total: 3.26s	remaining: 3m 35s
149:	learn: 1553017.9827520	total: 3.28s	remaining: 3m 35s
150:	learn: 1552062.5560477	total: 3.3s	remaining: 3m 35s
151:	learn: 1550920.4949820	total: 3.32s	remaining: 3m 35s
152:	learn: 1549515.1713314	total: 3.34s	remaining: 3m 35s
153:	learn: 1548328.7675423	total: 3.36s	remaining: 3m 35s
154:	learn: 1546659.3651722	total: 3.39s	remaining: 3m 35s
155:	learn: 1544232.2974246	total: 3.41s	remaining: 3m 35s
156:	learn: 1541491.5998403	total: 3.43s	remaining: 3m 35s
157:	learn: 1540027.8540031	total: 3.46s	remaining: 3m 35s
158:	learn: 1538896.1079564	total: 3.48s	remaining: 3m 35s
159:	learn: 1537566.1519125	total: 3.5s	remaining: 3m 35s
160:	learn: 1534924.1892657	total: 3.53s	remaining: 3m 35s

285:	learn: 1427510.0156845	total: 6.34s	remaining: 3m 35s
286:	learn: 1426906.4539434	total: 6.36s	remaining: 3m 35s
287:	learn: 1426435.9664169	total: 6.38s	remaining: 3m 35s
288:	learn: 1425953.9088416	total: 6.4s	remaining: 3m 35s
289:	learn: 1425159.3412287	total: 6.43s	remaining: 3m 35s
290:	learn: 1424496.5744998	total: 6.45s	remaining: 3m 35s
291:	learn: 1423926.2277499	total: 6.47s	remaining: 3m 35s
292:	learn: 1423490.0098319	total: 6.5s	remaining: 3m 35s
293:	learn: 1423053.8589179	total: 6.52s	remaining: 3m 35s
294:	learn: 1422584.6141088	total: 6.54s	remaining: 3m 35s
295:	learn: 1421960.8174489	total: 6.56s	remaining: 3m 35s
296:	learn: 1421404.6914295	total: 6.58s	remaining: 3m 35s
297:	learn: 1420981.7343660	total: 6.61s	remaining: 3m 35s
298:	learn: 1420442.1592094	total: 6.63s	remaining: 3m 35s
299:	learn: 1419796.2909447	total: 6.65s	remaining: 3m 35s
300:	learn: 1419184.9888491	total: 6.67s	remaining: 3m 35s
301:	learn: 1418618.0635010	total: 6.69s	remaining: 3m 34s

431:	learn: 1350184.0157870	total: 9.69s	remaining: 3m 34s
432:	learn: 1349807.6297633	total: 9.71s	remaining: 3m 34s
433:	learn: 1349544.6912129	total: 9.73s	remaining: 3m 34s
434:	learn: 1349288.1988553	total: 9.75s	remaining: 3m 34s
435:	learn: 1349087.0097282	total: 9.78s	remaining: 3m 34s
436:	learn: 1348707.0108200	total: 9.8s	remaining: 3m 34s
437:	learn: 1347779.2801104	total: 9.82s	remaining: 3m 34s
438:	learn: 1347386.4577650	total: 9.85s	remaining: 3m 34s
439:	learn: 1347071.9104394	total: 9.87s	remaining: 3m 34s
440:	learn: 1346729.4165673	total: 9.89s	remaining: 3m 34s
441:	learn: 1346508.6694373	total: 9.91s	remaining: 3m 34s
442:	learn: 1346256.1325759	total: 9.94s	remaining: 3m 34s
443:	learn: 1345292.3688813	total: 9.96s	remaining: 3m 34s
444:	learn: 1345056.5869448	total: 9.99s	remaining: 3m 34s
445:	learn: 1344799.0841025	total: 10s	remaining: 3m 34s
446:	learn: 1344060.4595150	total: 10s	remaining: 3m 34s
447:	learn: 1343809.2885138	total: 10.1s	remaining: 3m 34s
44

576:	learn: 1297874.1639723	total: 13s	remaining: 3m 31s
577:	learn: 1297536.8073726	total: 13s	remaining: 3m 31s
578:	learn: 1297202.8310783	total: 13s	remaining: 3m 31s
579:	learn: 1296998.3979444	total: 13s	remaining: 3m 31s
580:	learn: 1296749.0723260	total: 13s	remaining: 3m 31s
581:	learn: 1296435.1518922	total: 13.1s	remaining: 3m 31s
582:	learn: 1295909.6821829	total: 13.1s	remaining: 3m 31s
583:	learn: 1295644.7661120	total: 13.1s	remaining: 3m 31s
584:	learn: 1295292.0326606	total: 13.1s	remaining: 3m 31s
585:	learn: 1294908.7964860	total: 13.2s	remaining: 3m 31s
586:	learn: 1294621.9408728	total: 13.2s	remaining: 3m 31s
587:	learn: 1294224.5348685	total: 13.2s	remaining: 3m 31s
588:	learn: 1294075.0375670	total: 13.2s	remaining: 3m 31s
589:	learn: 1293703.1872070	total: 13.3s	remaining: 3m 31s
590:	learn: 1293438.0342890	total: 13.3s	remaining: 3m 31s
591:	learn: 1293121.7569915	total: 13.3s	remaining: 3m 31s
592:	learn: 1292869.8001536	total: 13.3s	remaining: 3m 31s
593:	le

...

9415:	learn: 838101.1050563	total: 3m 28s	remaining: 13s
9416:	learn: 838093.4364696	total: 3m 28s	remaining: 12.9s
9417:	learn: 838064.0752715	total: 3m 28s	remaining: 12.9s
9418:	learn: 838011.1314524	total: 3m 28s	remaining: 12.9s
9419:	learn: 837998.7596541	total: 3m 28s	remaining: 12.9s
9420:	learn: 837969.8278547	total: 3m 28s	remaining: 12.8s
9421:	learn: 837956.1343071	total: 3m 29s	remaining: 12.8s
9422:	learn: 837936.1952101	total: 3m 29s	remaining: 12.8s
9423:	learn: 837930.9519189	total: 3m 29s	remaining: 12.8s
9424:	learn: 837921.2781762	total: 3m 29s	remaining: 12.8s
9425:	learn: 837905.2800544	total: 3m 29s	remaining: 12.7s
9426:	learn: 837871.8239437	total: 3m 29s	remaining: 12.7s
9427:	learn: 837862.1893255	total: 3m 29s	remaining: 12.7s
9428:	learn: 837843.6124921	total: 3m 29s	remaining: 12.7s
9429:	learn: 837834.3599645	total: 3m 29s	remaining: 12.6s
9430:	learn: 837814.0297333	total: 3m 29s	remaining: 12.6s
9431:	learn: 837796.4538589	total: 3m 29s	remaining: 12.6s

9563:	learn: 835282.4384019	total: 3m 32s	remaining: 9.67s
9564:	learn: 835273.2071371	total: 3m 32s	remaining: 9.65s
9565:	learn: 835254.3273828	total: 3m 32s	remaining: 9.63s
9566:	learn: 835233.5305903	total: 3m 32s	remaining: 9.61s
9567:	learn: 835222.5914250	total: 3m 32s	remaining: 9.59s
9568:	learn: 835185.0284297	total: 3m 32s	remaining: 9.56s
9569:	learn: 835165.7082620	total: 3m 32s	remaining: 9.54s
9570:	learn: 835139.7653827	total: 3m 32s	remaining: 9.52s
9571:	learn: 835131.3432238	total: 3m 32s	remaining: 9.5s
9572:	learn: 835081.2166217	total: 3m 32s	remaining: 9.47s
9573:	learn: 835070.7459080	total: 3m 32s	remaining: 9.45s
9574:	learn: 835054.5448758	total: 3m 32s	remaining: 9.43s
9575:	learn: 835044.3396771	total: 3m 32s	remaining: 9.41s
9576:	learn: 835033.9678285	total: 3m 32s	remaining: 9.39s
9577:	learn: 835021.8798940	total: 3m 32s	remaining: 9.36s
9578:	learn: 835016.3480165	total: 3m 32s	remaining: 9.34s
9579:	learn: 834971.5065721	total: 3m 32s	remaining: 9.32

9705:	learn: 832647.7809072	total: 3m 35s	remaining: 6.53s
9706:	learn: 832634.7338998	total: 3m 35s	remaining: 6.51s
9707:	learn: 832611.4137002	total: 3m 35s	remaining: 6.49s
9708:	learn: 832590.5364532	total: 3m 35s	remaining: 6.46s
9709:	learn: 832580.2863082	total: 3m 35s	remaining: 6.44s
9710:	learn: 832517.9565532	total: 3m 35s	remaining: 6.42s
9711:	learn: 832515.6628179	total: 3m 35s	remaining: 6.4s
9712:	learn: 832496.2818420	total: 3m 35s	remaining: 6.37s
9713:	learn: 832469.8399630	total: 3m 35s	remaining: 6.35s
9714:	learn: 832462.7690978	total: 3m 35s	remaining: 6.33s
9715:	learn: 832409.3459604	total: 3m 35s	remaining: 6.31s
9716:	learn: 832385.1317932	total: 3m 35s	remaining: 6.29s
9717:	learn: 832377.0447022	total: 3m 35s	remaining: 6.26s
9718:	learn: 832369.2736329	total: 3m 35s	remaining: 6.24s
9719:	learn: 832346.2979065	total: 3m 35s	remaining: 6.22s
9720:	learn: 832340.4633349	total: 3m 35s	remaining: 6.2s
9721:	learn: 832332.8116335	total: 3m 35s	remaining: 6.17s

9847:	learn: 830055.6746662	total: 3m 38s	remaining: 3.38s
9848:	learn: 830043.3905637	total: 3m 38s	remaining: 3.35s
9849:	learn: 830025.3640286	total: 3m 38s	remaining: 3.33s
9850:	learn: 830013.4579075	total: 3m 38s	remaining: 3.31s
9851:	learn: 829995.3040603	total: 3m 38s	remaining: 3.29s
9852:	learn: 829984.4986459	total: 3m 38s	remaining: 3.26s
9853:	learn: 829969.5647398	total: 3m 38s	remaining: 3.24s
9854:	learn: 829956.3144061	total: 3m 38s	remaining: 3.22s
9855:	learn: 829943.4035296	total: 3m 38s	remaining: 3.2s
9856:	learn: 829934.0378038	total: 3m 38s	remaining: 3.17s
9857:	learn: 829920.4168672	total: 3m 38s	remaining: 3.15s
9858:	learn: 829909.2205367	total: 3m 38s	remaining: 3.13s
9859:	learn: 829860.5475236	total: 3m 38s	remaining: 3.11s
9860:	learn: 829847.6543405	total: 3m 39s	remaining: 3.09s
9861:	learn: 829834.5675280	total: 3m 39s	remaining: 3.06s
9862:	learn: 829819.4635282	total: 3m 39s	remaining: 3.04s
9863:	learn: 829802.7941365	total: 3m 39s	remaining: 3.02

9993:	learn: 827554.2252528	total: 3m 41s	remaining: 133ms
9994:	learn: 827536.6368713	total: 3m 41s	remaining: 111ms
9995:	learn: 827520.6559883	total: 3m 41s	remaining: 88.8ms
9996:	learn: 827491.6599377	total: 3m 42s	remaining: 66.6ms
9997:	learn: 827457.3642193	total: 3m 42s	remaining: 44.4ms
9998:	learn: 827446.4339946	total: 3m 42s	remaining: 22.2ms
9999:	learn: 827413.7806116	total: 3m 42s	remaining: 0us


In [35]:
#Using CatBoost model with 20000 iterations.
cat_model20000 = CatBoostRegressor(iterations = 20000).fit(train_copy[features_columns], train_copy["naira_price"])

0:	learn: 3749797.0492992	total: 26.2ms	remaining: 8m 43s
1:	learn: 3672608.9735922	total: 50.3ms	remaining: 8m 22s
2:	learn: 3597486.4017296	total: 74.6ms	remaining: 8m 17s
3:	learn: 3525744.5189320	total: 97.4ms	remaining: 8m 6s
4:	learn: 3455406.8642599	total: 119ms	remaining: 7m 55s
5:	learn: 3388086.1671816	total: 141ms	remaining: 7m 48s
6:	learn: 3324434.9159011	total: 164ms	remaining: 7m 48s
7:	learn: 3262238.5447145	total: 187ms	remaining: 7m 46s
8:	learn: 3202273.7923378	total: 208ms	remaining: 7m 42s
9:	learn: 3144501.7444038	total: 233ms	remaining: 7m 45s
10:	learn: 3088553.6554168	total: 257ms	remaining: 7m 47s
11:	learn: 3034854.1488539	total: 280ms	remaining: 7m 45s
12:	learn: 2982923.5069686	total: 305ms	remaining: 7m 48s
13:	learn: 2933189.9104814	total: 327ms	remaining: 7m 46s
14:	learn: 2885284.5338898	total: 349ms	remaining: 7m 45s
15:	learn: 2839680.2735827	total: 371ms	remaining: 7m 43s
16:	learn: 2794905.9434648	total: 394ms	remaining: 7m 42s
17:	learn: 2752166.05

145:	learn: 1558921.6316960	total: 3.36s	remaining: 7m 37s
146:	learn: 1557247.7901959	total: 3.39s	remaining: 7m 37s
147:	learn: 1555801.1770276	total: 3.41s	remaining: 7m 36s
148:	learn: 1554826.2940501	total: 3.43s	remaining: 7m 36s
149:	learn: 1553017.9827520	total: 3.45s	remaining: 7m 36s
150:	learn: 1552062.5560477	total: 3.47s	remaining: 7m 36s
151:	learn: 1550920.4949820	total: 3.5s	remaining: 7m 36s
152:	learn: 1549515.1713314	total: 3.52s	remaining: 7m 36s
153:	learn: 1548328.7675423	total: 3.54s	remaining: 7m 36s
154:	learn: 1546659.3651722	total: 3.57s	remaining: 7m 36s
155:	learn: 1544232.2974246	total: 3.59s	remaining: 7m 36s
156:	learn: 1541491.5998403	total: 3.61s	remaining: 7m 36s
157:	learn: 1540027.8540031	total: 3.64s	remaining: 7m 36s
158:	learn: 1538896.1079564	total: 3.66s	remaining: 7m 36s
159:	learn: 1537566.1519125	total: 3.68s	remaining: 7m 36s
160:	learn: 1534924.1892657	total: 3.71s	remaining: 7m 36s
161:	learn: 1533730.7876207	total: 3.73s	remaining: 7m 36

285:	learn: 1427510.0156845	total: 6.51s	remaining: 7m 28s
286:	learn: 1426906.4539434	total: 6.53s	remaining: 7m 28s
287:	learn: 1426435.9664169	total: 6.55s	remaining: 7m 28s
288:	learn: 1425953.9088416	total: 6.57s	remaining: 7m 28s
289:	learn: 1425159.3412287	total: 6.6s	remaining: 7m 28s
290:	learn: 1424496.5744998	total: 6.62s	remaining: 7m 28s
291:	learn: 1423926.2277499	total: 6.64s	remaining: 7m 28s
292:	learn: 1423490.0098319	total: 6.67s	remaining: 7m 28s
293:	learn: 1423053.8589179	total: 6.69s	remaining: 7m 28s
294:	learn: 1422584.6141088	total: 6.71s	remaining: 7m 28s
295:	learn: 1421960.8174489	total: 6.73s	remaining: 7m 28s
296:	learn: 1421404.6914295	total: 6.75s	remaining: 7m 28s
297:	learn: 1420981.7343660	total: 6.77s	remaining: 7m 27s
298:	learn: 1420442.1592094	total: 6.79s	remaining: 7m 27s
299:	learn: 1419796.2909447	total: 6.82s	remaining: 7m 27s
300:	learn: 1419184.9888491	total: 6.84s	remaining: 7m 27s
301:	learn: 1418618.0635010	total: 6.86s	remaining: 7m 27

433:	learn: 1349544.6912129	total: 9.84s	remaining: 7m 23s
434:	learn: 1349288.1988553	total: 9.87s	remaining: 7m 23s
435:	learn: 1349087.0097282	total: 9.89s	remaining: 7m 23s
436:	learn: 1348707.0108200	total: 9.91s	remaining: 7m 23s
437:	learn: 1347779.2801104	total: 9.94s	remaining: 7m 23s
438:	learn: 1347386.4577650	total: 9.96s	remaining: 7m 23s
439:	learn: 1347071.9104394	total: 9.98s	remaining: 7m 23s
440:	learn: 1346729.4165673	total: 10s	remaining: 7m 23s
441:	learn: 1346508.6694373	total: 10s	remaining: 7m 23s
442:	learn: 1346256.1325759	total: 10s	remaining: 7m 23s
443:	learn: 1345292.3688813	total: 10.1s	remaining: 7m 23s
444:	learn: 1345056.5869448	total: 10.1s	remaining: 7m 23s
445:	learn: 1344799.0841025	total: 10.1s	remaining: 7m 23s
446:	learn: 1344060.4595150	total: 10.1s	remaining: 7m 23s
447:	learn: 1343809.2885138	total: 10.2s	remaining: 7m 23s
448:	learn: 1342890.3570906	total: 10.2s	remaining: 7m 23s
449:	learn: 1342510.4856298	total: 10.2s	remaining: 7m 23s
450

578:	learn: 1297202.8310783	total: 13s	remaining: 7m 17s
579:	learn: 1296998.3979444	total: 13.1s	remaining: 7m 17s
580:	learn: 1296749.0723260	total: 13.1s	remaining: 7m 17s
581:	learn: 1296435.1518922	total: 13.1s	remaining: 7m 17s
582:	learn: 1295909.6821829	total: 13.1s	remaining: 7m 17s
583:	learn: 1295644.7661120	total: 13.2s	remaining: 7m 17s
584:	learn: 1295292.0326606	total: 13.2s	remaining: 7m 17s
585:	learn: 1294908.7964860	total: 13.2s	remaining: 7m 17s
586:	learn: 1294621.9408728	total: 13.2s	remaining: 7m 17s
587:	learn: 1294224.5348685	total: 13.2s	remaining: 7m 17s
588:	learn: 1294075.0375670	total: 13.3s	remaining: 7m 17s
589:	learn: 1293703.1872070	total: 13.3s	remaining: 7m 17s
590:	learn: 1293438.0342890	total: 13.3s	remaining: 7m 17s
591:	learn: 1293121.7569915	total: 13.3s	remaining: 7m 17s
592:	learn: 1292869.8001536	total: 13.4s	remaining: 7m 16s
593:	learn: 1292576.5938820	total: 13.4s	remaining: 7m 16s
594:	learn: 1292320.3540233	total: 13.4s	remaining: 7m 16s

...

19361:	learn: 711622.1550739	total: 7m 14s	remaining: 14.3s
19362:	learn: 711616.3278583	total: 7m 14s	remaining: 14.3s
19363:	learn: 711604.5631818	total: 7m 14s	remaining: 14.3s
19364:	learn: 711599.5273797	total: 7m 15s	remaining: 14.3s
19365:	learn: 711594.3069937	total: 7m 15s	remaining: 14.2s
19366:	learn: 711590.8638069	total: 7m 15s	remaining: 14.2s
19367:	learn: 711583.5680140	total: 7m 15s	remaining: 14.2s
19368:	learn: 711577.8729098	total: 7m 15s	remaining: 14.2s
19369:	learn: 711575.0941657	total: 7m 15s	remaining: 14.2s
19370:	learn: 711547.6838160	total: 7m 15s	remaining: 14.1s
19371:	learn: 711537.4669597	total: 7m 15s	remaining: 14.1s
19372:	learn: 711527.6182837	total: 7m 15s	remaining: 14.1s
19373:	learn: 711521.0489642	total: 7m 15s	remaining: 14.1s
19374:	learn: 711478.0617992	total: 7m 15s	remaining: 14s
19375:	learn: 711474.8568515	total: 7m 15s	remaining: 14s
19376:	learn: 711467.5849748	total: 7m 15s	remaining: 14s
19377:	learn: 711466.1170552	total: 7m 15s	rem

19502:	learn: 710506.3362109	total: 7m 18s	remaining: 11.2s
19503:	learn: 710501.7088045	total: 7m 18s	remaining: 11.1s
19504:	learn: 710497.0771075	total: 7m 18s	remaining: 11.1s
19505:	learn: 710484.7950217	total: 7m 18s	remaining: 11.1s
19506:	learn: 710465.8847286	total: 7m 18s	remaining: 11.1s
19507:	learn: 710457.4642717	total: 7m 18s	remaining: 11.1s
19508:	learn: 710448.0147505	total: 7m 18s	remaining: 11s
19509:	learn: 710443.8993105	total: 7m 18s	remaining: 11s
19510:	learn: 710438.7133827	total: 7m 18s	remaining: 11s
19511:	learn: 710433.5203178	total: 7m 18s	remaining: 11s
19512:	learn: 710406.6329924	total: 7m 18s	remaining: 10.9s
19513:	learn: 710402.3231567	total: 7m 18s	remaining: 10.9s
19514:	learn: 710395.9436894	total: 7m 18s	remaining: 10.9s
19515:	learn: 710388.2072288	total: 7m 18s	remaining: 10.9s
19516:	learn: 710380.7904940	total: 7m 18s	remaining: 10.8s
19517:	learn: 710378.4446406	total: 7m 18s	remaining: 10.8s
19518:	learn: 710373.1099019	total: 7m 18s	remai

19641:	learn: 709231.4874623	total: 7m 21s	remaining: 8.04s
19642:	learn: 709225.8196998	total: 7m 21s	remaining: 8.02s
19643:	learn: 709221.4150369	total: 7m 21s	remaining: 8s
19644:	learn: 709216.5491759	total: 7m 21s	remaining: 7.97s
19645:	learn: 709204.4979035	total: 7m 21s	remaining: 7.95s
19646:	learn: 709198.8546263	total: 7m 21s	remaining: 7.93s
19647:	learn: 709195.0286319	total: 7m 21s	remaining: 7.91s
19648:	learn: 709189.7643910	total: 7m 21s	remaining: 7.88s
19649:	learn: 709183.7691883	total: 7m 21s	remaining: 7.86s
19650:	learn: 709175.1615683	total: 7m 21s	remaining: 7.84s
19651:	learn: 709168.0026146	total: 7m 21s	remaining: 7.82s
19652:	learn: 709157.0084461	total: 7m 21s	remaining: 7.79s
19653:	learn: 709150.5079617	total: 7m 21s	remaining: 7.77s
19654:	learn: 709145.0764185	total: 7m 21s	remaining: 7.75s
19655:	learn: 709137.5166772	total: 7m 21s	remaining: 7.73s
19656:	learn: 709133.2270729	total: 7m 21s	remaining: 7.7s
19657:	learn: 709124.3334077	total: 7m 21s	r

19779:	learn: 708137.9851013	total: 7m 24s	remaining: 4.94s
19780:	learn: 708130.9562663	total: 7m 24s	remaining: 4.92s
19781:	learn: 708126.6785398	total: 7m 24s	remaining: 4.9s
19782:	learn: 708102.8388579	total: 7m 24s	remaining: 4.87s
19783:	learn: 708100.1776199	total: 7m 24s	remaining: 4.85s
19784:	learn: 708080.7717620	total: 7m 24s	remaining: 4.83s
19785:	learn: 708070.0206707	total: 7m 24s	remaining: 4.81s
19786:	learn: 708064.3869126	total: 7m 24s	remaining: 4.78s
19787:	learn: 708059.1639972	total: 7m 24s	remaining: 4.76s
19788:	learn: 708048.1261899	total: 7m 24s	remaining: 4.74s
19789:	learn: 708040.6599510	total: 7m 24s	remaining: 4.72s
19790:	learn: 708037.2870565	total: 7m 24s	remaining: 4.7s
19791:	learn: 708031.5396498	total: 7m 24s	remaining: 4.67s
19792:	learn: 708013.8437861	total: 7m 24s	remaining: 4.65s
19793:	learn: 708001.7890310	total: 7m 24s	remaining: 4.63s
19794:	learn: 707988.5522414	total: 7m 24s	remaining: 4.61s
19795:	learn: 707982.2500113	total: 7m 24s

19917:	learn: 707011.0900644	total: 7m 27s	remaining: 1.84s
19918:	learn: 707003.7873787	total: 7m 27s	remaining: 1.82s
19919:	learn: 706994.1535109	total: 7m 27s	remaining: 1.8s
19920:	learn: 706984.0610763	total: 7m 27s	remaining: 1.77s
19921:	learn: 706980.6881151	total: 7m 27s	remaining: 1.75s
19922:	learn: 706975.1892031	total: 7m 27s	remaining: 1.73s
19923:	learn: 706969.0599083	total: 7m 27s	remaining: 1.71s
19924:	learn: 706963.3091778	total: 7m 27s	remaining: 1.68s
19925:	learn: 706947.1245382	total: 7m 27s	remaining: 1.66s
19926:	learn: 706905.7255382	total: 7m 27s	remaining: 1.64s
19927:	learn: 706900.8712464	total: 7m 27s	remaining: 1.62s
19928:	learn: 706891.6707073	total: 7m 27s	remaining: 1.59s
19929:	learn: 706888.2965103	total: 7m 27s	remaining: 1.57s
19930:	learn: 706881.3990831	total: 7m 27s	remaining: 1.55s
19931:	learn: 706864.8446217	total: 7m 27s	remaining: 1.53s
19932:	learn: 706859.2542337	total: 7m 27s	remaining: 1.5s
19933:	learn: 706828.9240020	total: 7m 27s

In [ ]:
#Using CatBoost model with 40000 iterations.
cat_model40000 = CatBoostRegressor(iterations = 40000).fit(train_copy[features_columns], train_copy["naira_price"])

# ENsemble stuff:

In [185]:
from mlxtend.regressor import StackingRegressor
from mlxtend.regressor import LinearRegression

lr = LinearRegression()

In [187]:
eclf = StackingRegressor(regressors=[cat_model10000, cat_modelX000, cat_model1000,rf_model ],
                              meta_regressor=lr)

eclf = eclf.fit(train_copy[features_columns], train_copy["naira_price"])

0:	learn: 3749797.0492992	total: 25.6ms	remaining: 4m 15s
1:	learn: 3672608.9735922	total: 48.1ms	remaining: 4m
2:	learn: 3597486.4017296	total: 68.9ms	remaining: 3m 49s
3:	learn: 3525744.5189320	total: 91.2ms	remaining: 3m 48s
4:	learn: 3455406.8642599	total: 112ms	remaining: 3m 44s
5:	learn: 3388086.1671816	total: 133ms	remaining: 3m 41s
6:	learn: 3324434.9159011	total: 154ms	remaining: 3m 39s
7:	learn: 3262238.5447145	total: 174ms	remaining: 3m 37s
8:	learn: 3202273.7923378	total: 195ms	remaining: 3m 36s
9:	learn: 3144501.7444038	total: 215ms	remaining: 3m 34s
10:	learn: 3088553.6554168	total: 237ms	remaining: 3m 35s
11:	learn: 3034854.1488539	total: 258ms	remaining: 3m 34s
12:	learn: 2982923.5069686	total: 279ms	remaining: 3m 34s
13:	learn: 2933189.9104814	total: 299ms	remaining: 3m 33s
14:	learn: 2885284.5338898	total: 321ms	remaining: 3m 33s
15:	learn: 2839680.2735827	total: 343ms	remaining: 3m 34s
16:	learn: 2794905.9434648	total: 365ms	remaining: 3m 34s
17:	learn: 2752166.05641

142:	learn: 1562938.8399113	total: 3.21s	remaining: 3m 41s
143:	learn: 1561785.9320289	total: 3.24s	remaining: 3m 41s
144:	learn: 1560238.0275044	total: 3.26s	remaining: 3m 41s
145:	learn: 1558921.6316960	total: 3.28s	remaining: 3m 41s
146:	learn: 1557247.7901959	total: 3.3s	remaining: 3m 41s
147:	learn: 1555801.1770276	total: 3.32s	remaining: 3m 41s
148:	learn: 1554826.2940501	total: 3.35s	remaining: 3m 41s
149:	learn: 1553017.9827520	total: 3.37s	remaining: 3m 41s
150:	learn: 1552062.5560477	total: 3.39s	remaining: 3m 41s
151:	learn: 1550920.4949820	total: 3.42s	remaining: 3m 41s
152:	learn: 1549515.1713314	total: 3.44s	remaining: 3m 41s
153:	learn: 1548328.7675423	total: 3.46s	remaining: 3m 41s
154:	learn: 1546659.3651722	total: 3.48s	remaining: 3m 41s
155:	learn: 1544232.2974246	total: 3.5s	remaining: 3m 41s
156:	learn: 1541491.5998403	total: 3.53s	remaining: 3m 41s
157:	learn: 1540027.8540031	total: 3.55s	remaining: 3m 41s
158:	learn: 1538896.1079564	total: 3.57s	remaining: 3m 41s

283:	learn: 1428448.7012122	total: 6.36s	remaining: 3m 37s
284:	learn: 1428004.8866077	total: 6.38s	remaining: 3m 37s
285:	learn: 1427510.0156845	total: 6.4s	remaining: 3m 37s
286:	learn: 1426906.4539434	total: 6.42s	remaining: 3m 37s
287:	learn: 1426435.9664169	total: 6.45s	remaining: 3m 37s
288:	learn: 1425953.9088416	total: 6.47s	remaining: 3m 37s
289:	learn: 1425159.3412287	total: 6.49s	remaining: 3m 37s
290:	learn: 1424496.5744998	total: 6.51s	remaining: 3m 37s
291:	learn: 1423926.2277499	total: 6.54s	remaining: 3m 37s
292:	learn: 1423490.0098319	total: 6.56s	remaining: 3m 37s
293:	learn: 1423053.8589179	total: 6.58s	remaining: 3m 37s
294:	learn: 1422584.6141088	total: 6.6s	remaining: 3m 37s
295:	learn: 1421960.8174489	total: 6.62s	remaining: 3m 37s
296:	learn: 1421404.6914295	total: 6.65s	remaining: 3m 37s
297:	learn: 1420981.7343660	total: 6.67s	remaining: 3m 37s
298:	learn: 1420442.1592094	total: 6.69s	remaining: 3m 37s
299:	learn: 1419796.2909447	total: 6.71s	remaining: 3m 37s

430:	learn: 1350612.3136914	total: 9.65s	remaining: 3m 34s
431:	learn: 1350184.0157870	total: 9.67s	remaining: 3m 34s
432:	learn: 1349807.6297633	total: 9.69s	remaining: 3m 34s
433:	learn: 1349544.6912129	total: 9.71s	remaining: 3m 34s
434:	learn: 1349288.1988553	total: 9.73s	remaining: 3m 34s
435:	learn: 1349087.0097282	total: 9.76s	remaining: 3m 34s
436:	learn: 1348707.0108200	total: 9.78s	remaining: 3m 34s
437:	learn: 1347779.2801104	total: 9.8s	remaining: 3m 34s
438:	learn: 1347386.4577650	total: 9.83s	remaining: 3m 34s
439:	learn: 1347071.9104394	total: 9.85s	remaining: 3m 34s
440:	learn: 1346729.4165673	total: 9.87s	remaining: 3m 33s
441:	learn: 1346508.6694373	total: 9.89s	remaining: 3m 33s
442:	learn: 1346256.1325759	total: 9.91s	remaining: 3m 33s
443:	learn: 1345292.3688813	total: 9.94s	remaining: 3m 33s
444:	learn: 1345056.5869448	total: 9.96s	remaining: 3m 33s
445:	learn: 1344799.0841025	total: 9.99s	remaining: 3m 33s
446:	learn: 1344060.4595150	total: 10s	remaining: 3m 33s


573:	learn: 1298886.8845323	total: 12.8s	remaining: 3m 30s
574:	learn: 1298592.6679617	total: 12.8s	remaining: 3m 30s
575:	learn: 1298320.2908344	total: 12.9s	remaining: 3m 30s
576:	learn: 1297874.1639723	total: 12.9s	remaining: 3m 30s
577:	learn: 1297536.8073726	total: 12.9s	remaining: 3m 30s
578:	learn: 1297202.8310783	total: 12.9s	remaining: 3m 30s
579:	learn: 1296998.3979444	total: 13s	remaining: 3m 30s
580:	learn: 1296749.0723260	total: 13s	remaining: 3m 30s
581:	learn: 1296435.1518922	total: 13s	remaining: 3m 30s
582:	learn: 1295909.6821829	total: 13s	remaining: 3m 30s
583:	learn: 1295644.7661120	total: 13s	remaining: 3m 30s
584:	learn: 1295292.0326606	total: 13.1s	remaining: 3m 30s
585:	learn: 1294908.7964860	total: 13.1s	remaining: 3m 30s
586:	learn: 1294621.9408728	total: 13.1s	remaining: 3m 30s
587:	learn: 1294224.5348685	total: 13.1s	remaining: 3m 30s
588:	learn: 1294075.0375670	total: 13.2s	remaining: 3m 30s
589:	learn: 1293703.1872070	total: 13.2s	remaining: 3m 30s
590:	le

...

262:	learn: 1442672.3455535	total: 5.97s	remaining: 16.7s
263:	learn: 1441540.6742947	total: 5.99s	remaining: 16.7s
264:	learn: 1441179.0414740	total: 6.02s	remaining: 16.7s
265:	learn: 1440521.2050000	total: 6.04s	remaining: 16.7s
266:	learn: 1439641.3591567	total: 6.06s	remaining: 16.6s
267:	learn: 1439019.2369500	total: 6.08s	remaining: 16.6s
268:	learn: 1438625.1755627	total: 6.11s	remaining: 16.6s
269:	learn: 1436816.0082564	total: 6.13s	remaining: 16.6s
270:	learn: 1436298.5313429	total: 6.15s	remaining: 16.5s
271:	learn: 1435930.9371209	total: 6.17s	remaining: 16.5s
272:	learn: 1435405.7951792	total: 6.19s	remaining: 16.5s
273:	learn: 1434834.1579679	total: 6.22s	remaining: 16.5s
274:	learn: 1434468.9484661	total: 6.24s	remaining: 16.5s
275:	learn: 1434057.0818612	total: 6.26s	remaining: 16.4s
276:	learn: 1433272.6783659	total: 6.28s	remaining: 16.4s
277:	learn: 1432861.3327728	total: 6.3s	remaining: 16.4s
278:	learn: 1432227.8089331	total: 6.33s	remaining: 16.3s
279:	learn: 143

408:	learn: 1359058.2340654	total: 9.28s	remaining: 13.4s
409:	learn: 1358613.4056965	total: 9.3s	remaining: 13.4s
410:	learn: 1357878.1813059	total: 9.32s	remaining: 13.4s
411:	learn: 1357630.9396906	total: 9.34s	remaining: 13.3s
412:	learn: 1357195.2029487	total: 9.37s	remaining: 13.3s
413:	learn: 1356951.7709508	total: 9.39s	remaining: 13.3s
414:	learn: 1356357.2510851	total: 9.41s	remaining: 13.3s
415:	learn: 1355891.2191936	total: 9.44s	remaining: 13.2s
416:	learn: 1355782.2749457	total: 9.46s	remaining: 13.2s
417:	learn: 1355464.0585053	total: 9.48s	remaining: 13.2s
418:	learn: 1354877.1339317	total: 9.5s	remaining: 13.2s
419:	learn: 1354563.3201559	total: 9.53s	remaining: 13.2s
420:	learn: 1354348.6826449	total: 9.55s	remaining: 13.1s
421:	learn: 1354186.6359872	total: 9.57s	remaining: 13.1s
422:	learn: 1353662.5431272	total: 9.6s	remaining: 13.1s
423:	learn: 1353198.5880539	total: 9.62s	remaining: 13.1s
424:	learn: 1352902.5869093	total: 9.64s	remaining: 13s
425:	learn: 1352379

558:	learn: 1304030.5369971	total: 12.6s	remaining: 9.97s
559:	learn: 1303784.7014441	total: 12.7s	remaining: 9.95s
560:	learn: 1303366.5413155	total: 12.7s	remaining: 9.93s
561:	learn: 1303241.2635245	total: 12.7s	remaining: 9.9s
562:	learn: 1302784.7325470	total: 12.7s	remaining: 9.88s
563:	learn: 1302466.5524172	total: 12.8s	remaining: 9.86s
564:	learn: 1302114.6682918	total: 12.8s	remaining: 9.83s
565:	learn: 1301879.6054805	total: 12.8s	remaining: 9.81s
566:	learn: 1301439.8715792	total: 12.8s	remaining: 9.79s
567:	learn: 1301233.3565986	total: 12.8s	remaining: 9.76s
568:	learn: 1300980.2354806	total: 12.9s	remaining: 9.74s
569:	learn: 1300173.7964063	total: 12.9s	remaining: 9.72s
570:	learn: 1299675.3492820	total: 12.9s	remaining: 9.7s
571:	learn: 1299394.2737827	total: 12.9s	remaining: 9.67s
572:	learn: 1299090.8827186	total: 12.9s	remaining: 9.65s
573:	learn: 1298886.8845323	total: 13s	remaining: 9.63s
574:	learn: 1298592.6679617	total: 13s	remaining: 9.6s
575:	learn: 1298320.2

708:	learn: 1260227.5475619	total: 16s	remaining: 6.56s
709:	learn: 1260081.5261047	total: 16s	remaining: 6.54s
710:	learn: 1259612.3788807	total: 16s	remaining: 6.51s
711:	learn: 1259272.6542721	total: 16.1s	remaining: 6.49s
712:	learn: 1258910.1709973	total: 16.1s	remaining: 6.47s
713:	learn: 1258787.3832643	total: 16.1s	remaining: 6.45s
714:	learn: 1258558.0362119	total: 16.1s	remaining: 6.42s
715:	learn: 1258286.5138923	total: 16.1s	remaining: 6.4s
716:	learn: 1258136.0735973	total: 16.2s	remaining: 6.38s
717:	learn: 1257717.7265500	total: 16.2s	remaining: 6.36s
718:	learn: 1257466.3814890	total: 16.2s	remaining: 6.34s
719:	learn: 1257291.0378687	total: 16.2s	remaining: 6.31s
720:	learn: 1257165.2264191	total: 16.3s	remaining: 6.29s
721:	learn: 1256989.3530188	total: 16.3s	remaining: 6.27s
722:	learn: 1256674.3442072	total: 16.3s	remaining: 6.25s
723:	learn: 1256536.9439273	total: 16.3s	remaining: 6.22s
724:	learn: 1256057.5416735	total: 16.4s	remaining: 6.2s
725:	learn: 1255793.44

860:	learn: 1230685.8571676	total: 19.4s	remaining: 3.13s
861:	learn: 1230505.0591851	total: 19.4s	remaining: 3.1s
862:	learn: 1230335.2310972	total: 19.4s	remaining: 3.08s
863:	learn: 1230176.4329246	total: 19.4s	remaining: 3.06s
864:	learn: 1230030.7674350	total: 19.5s	remaining: 3.04s
865:	learn: 1229928.2478998	total: 19.5s	remaining: 3.01s
866:	learn: 1229818.4571064	total: 19.5s	remaining: 2.99s
867:	learn: 1229691.5134955	total: 19.5s	remaining: 2.97s
868:	learn: 1229542.4735683	total: 19.6s	remaining: 2.95s
869:	learn: 1229095.0103669	total: 19.6s	remaining: 2.92s
870:	learn: 1228976.0954027	total: 19.6s	remaining: 2.9s
871:	learn: 1228687.8928174	total: 19.6s	remaining: 2.88s
872:	learn: 1228557.4174434	total: 19.6s	remaining: 2.86s
873:	learn: 1228481.4743904	total: 19.7s	remaining: 2.83s
874:	learn: 1228354.0117247	total: 19.7s	remaining: 2.81s
875:	learn: 1228105.0515945	total: 19.7s	remaining: 2.79s
876:	learn: 1227837.5834684	total: 19.7s	remaining: 2.77s
877:	learn: 1227

In [105]:
mileage_mode = 0#zero_test["mileage"].mode()
temp = np.asarray(zero_test["mileage"])
temp = np.where(temp == 'kleinwagen', mileage_mode, temp)
zero_test["mileage"] = temp.astype(int)

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  This is separate from the ipykernel package so we can avoid doing imports until


In [106]:
zero_test["repair_status"].unique()

array([0, 'No', 'Yes'], dtype=object)

In [107]:
temp = np.asarray(zero_test["repair_status"])
temp = np.where(temp == 'nein', "No", temp)
temp = np.where(temp == 'ja', 'Yes', temp)
zero_test["repair_status"] = temp

In [108]:
zero_test["repair_status"].unique()

array([0, 'No', 'Yes'], dtype=object)

In [109]:
test_copy = zero_test.copy()

In [110]:
test_copy["car_type"] = test_copy["car_type"].replace([0], "a")#test_copy["car_type"].mode() )
test_copy["gas_type"] = test_copy["gas_type"].replace([0], "a")#test_copy["gas_type"].mode() )
test_copy["car_brand"] = test_copy["car_brand"].replace([0], "a")#test_copy["car_brand"].mode() )
test_copy["repair_status"] = test_copy["repair_status"].replace([0], "a")#test_copy["repair_status"].mode() )
test_copy["gear_type"] = test_copy["gear_type"].replace([0], "a")#test_copy["gear_type"].mode() )
test_copy["model"] = test_copy["model"].replace([0], "a")#test_copy["model"].mode() )

In [29]:
#encoder_dict = {}
#for column in string_columns:
#    encoder_dict[column] = LabelEncoder().fit(test_copy[column])

In [111]:
# Transforming string columns:
for column in string_columns:
    print(column)
    test_copy[column] = encoder_dict[column].transform(test_copy[column])

car_type
gas_type
car_brand
repair_status
gear_type
model


In [112]:
test_copy[date_colums] = test_copy[date_colums].apply(pd.to_datetime)

In [113]:
test_copy['scrapped_date'] = pd.to_datetime(test_copy['scrapped_date']).astype(int)/ 10**9
test_copy['date_of_advert'] = pd.to_datetime(test_copy['date_of_advert']).astype(int)/ 10**9
test_copy['last_advert_online'] = pd.to_datetime(test_copy['last_advert_online']).astype(int)/ 10**9

In [34]:
test_predictions = cat_model1000.predict(test_copy[features_columns])

test_submission = pd.DataFrame({"id" : zero_test["ID"], "naira_price" : np.round(test_predictions, decimals=1)})

test_submission.to_csv("dsn-car-price-zero-cat1000.csv", index=False)

# Now trying to combine the previous dataset with test_copy.

In [118]:
test_olddf = pd.read_csv("test.csv")
train_olddf = pd.read_csv("train.csv")

In [119]:
train_olddf.head(2)

id seller_type country_of_use weblog_date  Area_address_code  \
0   0     private         london  2016-03-24              66954   
1   1     private         london  2016-03-14              90480   

                         car_name car_type  Permit_registration_year  \
0            A5_Sportback_2.7_Tdi    coupé                      2013   
1  Jeep_Grand_Cherokee_"Overland"      NaN                      2006   

   registration_month  horse_power   mileage gas_type car_brand  \
0                   5          190  201125.0   diesel      audi   
1                   8          163  201125.0   diesel      jeep   

  Status_of_car_repair  gear_type date_of_advert last_advert_online  model  \
0                   ja    manuell     2016-03-24         2016-04-07    NaN   
1                  NaN  automatik     2016-03-14         2016-04-05  grand   

   naira_price  
0    6588000.0  
1    3528000.0

In [120]:
#df.rename(columns={"A": "a", "B": "b", "C": "c"}, errors="raise")
train_olddf = train_olddf.rename(columns={i:j for i,j in zip(train_olddf.columns, train_copy.columns)} )

In [121]:
train_olddf.head(2)

ID seller_type country_of_use scrapped_date  postal_code  \
0   0     private         london    2016-03-24        66954   
1   1     private         london    2016-03-14        90480   

                         car_name car_type  year_of_registration  \
0            A5_Sportback_2.7_Tdi    coupé                  2013   
1  Jeep_Grand_Cherokee_"Overland"      NaN                  2006   

   registration_month  horse_power   mileage gas_type car_brand repair_status  \
0                   5          190  201125.0   diesel      audi            ja   
1                   8          163  201125.0   diesel      jeep           NaN   

   gear_type date_of_advert last_advert_online  model  naira_price  
0    manuell     2016-03-24         2016-04-07    NaN    6588000.0  
1  automatik     2016-03-14         2016-04-05  grand    3528000.0

In [122]:
train_copy_old = train_olddf.copy().replace(np.nan, 0)
train_copy_new = train_olddf.copy()

In [123]:
train_copy_old["repair_status"].unique()

array(['ja', 0, 'nein'], dtype=object)

In [124]:
zero_train["repair_status"].unique()

array(['Yes', 'No', 0], dtype=object)

In [125]:
#Replacing repair_status values in train_copy_old:
temp = np.asarray(train_copy_old["repair_status"])
temp = np.where(temp == 'ja', 'Yes', temp)
temp = np.where(temp == 'nein', 'No', temp)
train_copy_old["repair_status"] = temp

In [126]:
train_copy_old["repair_status"].unique()

array(['Yes', 0, 'No'], dtype=object)

In [127]:
#For label encoding to work... Replcaing int 0 with "a" - it would still be transformed to 0.
#Replacing 0 with the modes instead.

train_copy_old["car_type"] = train_copy_old["car_type"].replace([0], "a")#train_copy_old["car_type"].mode() )
train_copy_old["gas_type"] = train_copy_old["gas_type"].replace([0], "a")#train_copy_old["gas_type"].mode() )
train_copy_old["car_brand"] = train_copy_old["car_brand"].replace([0], "a")#train_copy_old["car_brand"].mode() )
train_copy_old["repair_status"] = train_copy_old["repair_status"].replace([0], "a")#train_copy_old["repair_status"].mode() )
train_copy_old["gear_type"] = train_copy_old["gear_type"].replace([0], "a")#train_copy_old["gear_type"].mode() )
train_copy_old["model"] = train_copy_old["model"].replace([0], "a")#train_copy_old["model"].mode() )

# Transforming string columns:
for column in string_columns:
    print(column)
    train_copy_old[column] = encoder_dict[column].transform(train_copy_old[column])

train_copy_old[date_colums] = train_copy_old[date_colums].apply(pd.to_datetime)

train_copy_old['scrapped_date'] = pd.to_datetime(train_copy_old['scrapped_date']).astype(int)/ 10**9
train_copy_old['date_of_advert'] = pd.to_datetime(train_copy_old['date_of_advert']).astype(int)/ 10**9
train_copy_old['last_advert_online'] = pd.to_datetime(train_copy_old['last_advert_online']).astype(int)/ 10**9


car_type
gas_type
car_brand
repair_status
gear_type
model


In [128]:
train_copy_old.head()

ID seller_type country_of_use  scrapped_date  postal_code  \
0   0     private         london   1.458778e+09        66954   
1   1     private         london   1.457914e+09        90480   
2   3     private         london   1.459382e+09        60437   
3   4     private         london   1.459728e+09        33775   
4   5     private         london   1.459469e+09        67112   

                                            car_name  car_type  \
0                               A5_Sportback_2.7_Tdi         3   
1                     Jeep_Grand_Cherokee_"Overland"         0   
2                     Skoda_Fabia_1.4_TDI_PD_Classic         6   
3  BMW_316i___e36_Limousine___Bastlerfahrzeug__Ex...         4   
4                        Peugeot_206_CC_110_Platinum         2   

   year_of_registration  registration_month  horse_power   mileage  gas_type  \
0                  2013                   5          190  201125.0         2   
1                  2006                   8          163  201125.0         2   
2                  2010                   7           69  144810.0         2   
3                  1997                  10          102  241350.0         3   
4                  2006                   8          109  241350.0         3   

   car_brand  repair_status  gear_type  date_of_advert  last_advert_online  \
0          2              1          4    1.458778e+09        1.459987e+09   
1         15              2          3    1.457914e+09        1.459814e+09   
2         31              0          4    1.459382e+09        1.459901e+09   
3          3              1          4    1.459728e+09        1.459901e+09   
4         25              0          4    1.459469e+09        1.459814e+09   

   model  naira_price  
0     26    6588000.0  
1    120    3528000.0  
2    104    1296000.0  
3     11     234000.0  
4      8     792000.0

In [129]:
train_copy.head()

ID seller_type country_of_use  scrapped_date  postal_code  \
0   1     private         london   1.458778e+09        66954   
1   3     private         london   1.458173e+09        91074   
2   4     private         london   1.459382e+09        60437   
3   5     private         london   1.459728e+09        33775   
4   8     private         london   1.458173e+09        27472   

                                            car_name  car_type  \
0                               A5_Sportback_2.7_Tdi         3   
1                                 GOLF_4_1_4__3TÜRER         6   
2                     Skoda_Fabia_1.4_TDI_PD_Classic         6   
3  BMW_316i___e36_Limousine___Bastlerfahrzeug__Ex...         4   
4  VW_Golf_4_5_tuerig_zu_verkaufen_mit_Anhaengerk...         6   

   year_of_registration registration_month  horse_power   mileage  gas_type  \
0                  2013                  5          190  201125.0         2   
1                  2003                  6           75  241350.0         3   
2                  2010                  7           69  144810.0         2   
3                  1997                 10          102  241350.0         3   
4                  2000                  0          101  241350.0         0   

   car_brand  repair_status  gear_type  date_of_advert  last_advert_online  \
0          2              1          4    1.458778e+09        1.467590e+09   
1         39              0          4    1.458173e+09        1.458173e+09   
2         31              0          4    1.459382e+09        1.464998e+09   
3          3              1          4    1.459728e+09        1.464998e+09   
4         39              2          4    1.458173e+09        1.459382e+09   

   model  naira_price  
0     26    6588000.0  
1    119     540000.0  
2    104    1296000.0  
3     11     234000.0  
4    119     359640.0

In [ ]:
# Using new data train set model on previous data train set.

In [148]:
oldpred = xgb_model.predict(train_copy[features_columns])
metric_score = mean_squared_error(train_copy['naira_price'], oldpred)
print("Metric Score: ", sqrt(metric_score) )


Metric Score:  867732.5024757098


In [130]:
merged_train = pd.concat([train_copy, train_copy_old]).reset_index(drop=True)

In [131]:
merged_train.head()

ID seller_type country_of_use  scrapped_date  postal_code  \
0   1     private         london   1.458778e+09        66954   
1   3     private         london   1.458173e+09        91074   
2   4     private         london   1.459382e+09        60437   
3   5     private         london   1.459728e+09        33775   
4   8     private         london   1.458173e+09        27472   

                                            car_name  car_type  \
0                               A5_Sportback_2.7_Tdi         3   
1                                 GOLF_4_1_4__3TÜRER         6   
2                     Skoda_Fabia_1.4_TDI_PD_Classic         6   
3  BMW_316i___e36_Limousine___Bastlerfahrzeug__Ex...         4   
4  VW_Golf_4_5_tuerig_zu_verkaufen_mit_Anhaengerk...         6   

   year_of_registration registration_month  horse_power   mileage  gas_type  \
0                  2013                  5          190  201125.0         2   
1                  2003                  6           75  241350.0         3   
2                  2010                  7           69  144810.0         2   
3                  1997                 10          102  241350.0         3   
4                  2000                  0          101  241350.0         0   

   car_brand  repair_status  gear_type  date_of_advert  last_advert_online  \
0          2              1          4    1.458778e+09        1.467590e+09   
1         39              0          4    1.458173e+09        1.458173e+09   
2         31              0          4    1.459382e+09        1.464998e+09   
3          3              1          4    1.459728e+09        1.464998e+09   
4         39              2          4    1.458173e+09        1.459382e+09   

   model  naira_price  
0     26    6588000.0  
1    119     540000.0  
2    104    1296000.0  
3     11     234000.0  
4    119     359640.0

In [132]:
[len(train_copy), len(train_copy_old), len(merged_train)]

[224537, 234829, 459366]

In [174]:
cat_model1000 = CatBoostRegressor(iterations = 1000, depth=12).fit(merged_train[features_columns], merged_train['naira_price'])


0:	learn: 3735974.1828827	total: 189ms	remaining: 3m 8s
1:	learn: 3649918.6384365	total: 308ms	remaining: 2m 33s
2:	learn: 3567674.8354312	total: 426ms	remaining: 2m 21s
3:	learn: 3488250.5746773	total: 542ms	remaining: 2m 15s
4:	learn: 3411548.2170744	total: 661ms	remaining: 2m 11s
5:	learn: 3338401.1154646	total: 780ms	remaining: 2m 9s
6:	learn: 3266588.3477526	total: 899ms	remaining: 2m 7s
7:	learn: 3196488.8581261	total: 1.02s	remaining: 2m 7s
8:	learn: 3129419.1211087	total: 1.14s	remaining: 2m 5s
9:	learn: 3064303.6256004	total: 1.26s	remaining: 2m 4s
10:	learn: 3001824.9259280	total: 1.38s	remaining: 2m 4s
11:	learn: 2941403.8588326	total: 1.5s	remaining: 2m 3s
12:	learn: 2884361.1445357	total: 1.61s	remaining: 2m 2s
13:	learn: 2828632.0362295	total: 1.75s	remaining: 2m 3s
14:	learn: 2773541.4617185	total: 1.89s	remaining: 2m 3s
15:	learn: 2720308.2953899	total: 2.02s	remaining: 2m 4s
16:	learn: 2668938.7448270	total: 2.16s	remaining: 2m 4s
17:	learn: 2620176.8150007	total: 2.3s

144:	learn: 1258151.4172732	total: 19.2s	remaining: 1m 53s
145:	learn: 1256396.7551483	total: 19.3s	remaining: 1m 53s
146:	learn: 1254718.2468814	total: 19.4s	remaining: 1m 52s
147:	learn: 1253224.4472520	total: 19.6s	remaining: 1m 52s
148:	learn: 1251339.6254092	total: 19.7s	remaining: 1m 52s
149:	learn: 1250056.8289098	total: 19.8s	remaining: 1m 52s
150:	learn: 1248466.3501474	total: 20s	remaining: 1m 52s
151:	learn: 1246750.5801323	total: 20.1s	remaining: 1m 52s
152:	learn: 1245500.5208082	total: 20.3s	remaining: 1m 52s
153:	learn: 1244397.5577724	total: 20.4s	remaining: 1m 52s
154:	learn: 1242867.8803669	total: 20.5s	remaining: 1m 51s
155:	learn: 1241325.7841059	total: 20.7s	remaining: 1m 51s
156:	learn: 1240084.8138745	total: 20.8s	remaining: 1m 51s
157:	learn: 1237958.4148590	total: 20.9s	remaining: 1m 51s
158:	learn: 1236844.9461960	total: 21.1s	remaining: 1m 51s
159:	learn: 1235821.2005991	total: 21.2s	remaining: 1m 51s
160:	learn: 1234310.3992533	total: 21.4s	remaining: 1m 51s

284:	learn: 1122595.7214074	total: 38.2s	remaining: 1m 35s
285:	learn: 1122020.1027762	total: 38.3s	remaining: 1m 35s
286:	learn: 1121429.0397016	total: 38.4s	remaining: 1m 35s
287:	learn: 1120793.3032005	total: 38.6s	remaining: 1m 35s
288:	learn: 1120152.3176145	total: 38.7s	remaining: 1m 35s
289:	learn: 1119709.2373056	total: 38.8s	remaining: 1m 35s
290:	learn: 1119168.7067050	total: 39s	remaining: 1m 34s
291:	learn: 1118254.4002887	total: 39.1s	remaining: 1m 34s
292:	learn: 1117683.6288604	total: 39.2s	remaining: 1m 34s
293:	learn: 1116897.8848170	total: 39.4s	remaining: 1m 34s
294:	learn: 1115955.0329072	total: 39.5s	remaining: 1m 34s
295:	learn: 1115364.1139382	total: 39.6s	remaining: 1m 34s
296:	learn: 1114483.6352071	total: 39.8s	remaining: 1m 34s
297:	learn: 1113900.4760025	total: 39.9s	remaining: 1m 34s
298:	learn: 1113368.2505448	total: 40s	remaining: 1m 33s
299:	learn: 1112612.7269338	total: 40.2s	remaining: 1m 33s
300:	learn: 1112091.3875404	total: 40.3s	remaining: 1m 33s
3

424:	learn: 1041924.7881701	total: 56.9s	remaining: 1m 17s
425:	learn: 1041498.7622799	total: 57.1s	remaining: 1m 16s
426:	learn: 1040935.9910273	total: 57.2s	remaining: 1m 16s
427:	learn: 1040591.9588529	total: 57.3s	remaining: 1m 16s
428:	learn: 1040357.2016605	total: 57.5s	remaining: 1m 16s
429:	learn: 1039882.1319410	total: 57.6s	remaining: 1m 16s
430:	learn: 1039180.3846827	total: 57.7s	remaining: 1m 16s
431:	learn: 1038605.3654187	total: 57.9s	remaining: 1m 16s
432:	learn: 1038019.9184706	total: 58s	remaining: 1m 15s
433:	learn: 1037408.2796448	total: 58.1s	remaining: 1m 15s
434:	learn: 1036801.0488776	total: 58.3s	remaining: 1m 15s
435:	learn: 1036474.3771543	total: 58.4s	remaining: 1m 15s
436:	learn: 1036102.6177762	total: 58.5s	remaining: 1m 15s
437:	learn: 1035662.0136206	total: 58.7s	remaining: 1m 15s
438:	learn: 1035231.1950859	total: 58.8s	remaining: 1m 15s
439:	learn: 1034774.0721247	total: 58.9s	remaining: 1m 15s
440:	learn: 1034362.7564918	total: 59.1s	remaining: 1m 14s

567:	learn: 981501.0494891	total: 1m 15s	remaining: 57.7s
568:	learn: 981106.6165900	total: 1m 16s	remaining: 57.6s
569:	learn: 980870.8963170	total: 1m 16s	remaining: 57.5s
570:	learn: 980443.0255542	total: 1m 16s	remaining: 57.3s
571:	learn: 980064.7133784	total: 1m 16s	remaining: 57.2s
572:	learn: 979647.8774415	total: 1m 16s	remaining: 57.1s
573:	learn: 979317.5017432	total: 1m 16s	remaining: 56.9s
574:	learn: 979052.1622179	total: 1m 16s	remaining: 56.8s
575:	learn: 978793.2711056	total: 1m 16s	remaining: 56.7s
576:	learn: 978317.8402168	total: 1m 17s	remaining: 56.5s
577:	learn: 977952.1340917	total: 1m 17s	remaining: 56.4s
578:	learn: 977467.5563529	total: 1m 17s	remaining: 56.3s
579:	learn: 977109.0810627	total: 1m 17s	remaining: 56.1s
580:	learn: 976831.0086969	total: 1m 17s	remaining: 56s
581:	learn: 976552.7422124	total: 1m 17s	remaining: 55.9s
582:	learn: 976092.0561132	total: 1m 17s	remaining: 55.7s
583:	learn: 975772.1326516	total: 1m 18s	remaining: 55.6s
584:	learn: 9753

709:	learn: 933657.4845890	total: 1m 34s	remaining: 38.7s
710:	learn: 933470.6637969	total: 1m 34s	remaining: 38.6s
711:	learn: 933166.0774284	total: 1m 34s	remaining: 38.4s
712:	learn: 932998.5298594	total: 1m 35s	remaining: 38.3s
713:	learn: 932622.6108457	total: 1m 35s	remaining: 38.2s
714:	learn: 932380.0540848	total: 1m 35s	remaining: 38s
715:	learn: 932123.4498147	total: 1m 35s	remaining: 37.9s
716:	learn: 931842.5172178	total: 1m 35s	remaining: 37.7s
717:	learn: 931508.1240590	total: 1m 35s	remaining: 37.6s
718:	learn: 931203.3272867	total: 1m 35s	remaining: 37.5s
719:	learn: 930993.8017793	total: 1m 36s	remaining: 37.3s
720:	learn: 930650.2829345	total: 1m 36s	remaining: 37.2s
721:	learn: 930373.1898703	total: 1m 36s	remaining: 37.1s
722:	learn: 930082.8117408	total: 1m 36s	remaining: 36.9s
723:	learn: 929927.2940730	total: 1m 36s	remaining: 36.8s
724:	learn: 929652.4424482	total: 1m 36s	remaining: 36.7s
725:	learn: 929295.3122165	total: 1m 36s	remaining: 36.5s
726:	learn: 9287

851:	learn: 895582.0516905	total: 1m 53s	remaining: 19.7s
852:	learn: 895477.7789593	total: 1m 53s	remaining: 19.6s
853:	learn: 895357.5440339	total: 1m 53s	remaining: 19.5s
854:	learn: 895171.5356034	total: 1m 53s	remaining: 19.3s
855:	learn: 895010.9748232	total: 1m 54s	remaining: 19.2s
856:	learn: 894674.9697226	total: 1m 54s	remaining: 19.1s
857:	learn: 894392.7411366	total: 1m 54s	remaining: 18.9s
858:	learn: 894188.7368037	total: 1m 54s	remaining: 18.8s
859:	learn: 894013.5028017	total: 1m 54s	remaining: 18.6s
860:	learn: 893714.1715563	total: 1m 54s	remaining: 18.5s
861:	learn: 893537.7772069	total: 1m 54s	remaining: 18.4s
862:	learn: 893277.4241842	total: 1m 54s	remaining: 18.3s
863:	learn: 892910.8204485	total: 1m 55s	remaining: 18.1s
864:	learn: 892707.2657511	total: 1m 55s	remaining: 18s
865:	learn: 892561.3198830	total: 1m 55s	remaining: 17.9s
866:	learn: 892401.5803872	total: 1m 55s	remaining: 17.7s
867:	learn: 892139.4515452	total: 1m 55s	remaining: 17.6s
868:	learn: 8919

995:	learn: 864679.1873435	total: 2m 12s	remaining: 532ms
996:	learn: 864577.6822117	total: 2m 12s	remaining: 399ms
997:	learn: 864249.4432383	total: 2m 12s	remaining: 266ms
998:	learn: 864030.7161472	total: 2m 12s	remaining: 133ms
999:	learn: 863855.2267835	total: 2m 13s	remaining: 0us


In [172]:
from mlxtend.regressor import StackingRegressor
from mlxtend.regressor import LinearRegression

lr = LinearRegression()

xgb_model = xgb.XGBRegressor(max_depth=10)
cat_model1000 = CatBoostRegressor(iterations = 1000, depth=12)
eclf = StackingRegressor(regressors=[cat_model1000, xgb_model ],
                              meta_regressor=lr)

eclf = eclf.fit(merged_train[features_columns], merged_train['naira_price'])

0:	learn: 3735974.1828827	total: 182ms	remaining: 3m 1s
1:	learn: 3649918.6384365	total: 300ms	remaining: 2m 29s
2:	learn: 3567674.8354312	total: 416ms	remaining: 2m 18s
3:	learn: 3488250.5746773	total: 533ms	remaining: 2m 12s
4:	learn: 3411548.2170744	total: 654ms	remaining: 2m 10s
5:	learn: 3338401.1154646	total: 759ms	remaining: 2m 5s
6:	learn: 3266588.3477526	total: 870ms	remaining: 2m 3s
7:	learn: 3196488.8581261	total: 986ms	remaining: 2m 2s
8:	learn: 3129419.1211087	total: 1.1s	remaining: 2m 1s
9:	learn: 3064303.6256004	total: 1.22s	remaining: 2m
10:	learn: 3001824.9259280	total: 1.33s	remaining: 1m 59s
11:	learn: 2941403.8588326	total: 1.45s	remaining: 1m 59s
12:	learn: 2884361.1445357	total: 1.58s	remaining: 1m 59s
13:	learn: 2828632.0362295	total: 1.71s	remaining: 2m
14:	learn: 2773541.4617185	total: 1.84s	remaining: 2m 1s
15:	learn: 2720308.2953899	total: 1.98s	remaining: 2m 1s
16:	learn: 2668938.7448270	total: 2.11s	remaining: 2m 1s
17:	learn: 2620176.8150007	total: 2.24s	r

144:	learn: 1258151.4172732	total: 18.6s	remaining: 1m 49s
145:	learn: 1256396.7551483	total: 18.8s	remaining: 1m 49s
146:	learn: 1254718.2468814	total: 18.9s	remaining: 1m 49s
147:	learn: 1253224.4472520	total: 19s	remaining: 1m 49s
148:	learn: 1251339.6254092	total: 19.2s	remaining: 1m 49s
149:	learn: 1250056.8289098	total: 19.3s	remaining: 1m 49s
150:	learn: 1248466.3501474	total: 19.4s	remaining: 1m 49s
151:	learn: 1246750.5801323	total: 19.5s	remaining: 1m 49s
152:	learn: 1245500.5208082	total: 19.7s	remaining: 1m 48s
153:	learn: 1244397.5577724	total: 19.8s	remaining: 1m 48s
154:	learn: 1242867.8803669	total: 19.9s	remaining: 1m 48s
155:	learn: 1241325.7841059	total: 20.1s	remaining: 1m 48s
156:	learn: 1240084.8138745	total: 20.2s	remaining: 1m 48s
157:	learn: 1237958.4148590	total: 20.3s	remaining: 1m 48s
158:	learn: 1236844.9461960	total: 20.4s	remaining: 1m 48s
159:	learn: 1235821.2005991	total: 20.6s	remaining: 1m 47s
160:	learn: 1234310.3992533	total: 20.7s	remaining: 1m 47s

284:	learn: 1122595.7214074	total: 36.5s	remaining: 1m 31s
285:	learn: 1122020.1027762	total: 36.6s	remaining: 1m 31s
286:	learn: 1121429.0397016	total: 36.8s	remaining: 1m 31s
287:	learn: 1120793.3032005	total: 36.9s	remaining: 1m 31s
288:	learn: 1120152.3176145	total: 37s	remaining: 1m 31s
289:	learn: 1119709.2373056	total: 37.2s	remaining: 1m 30s
290:	learn: 1119168.7067050	total: 37.3s	remaining: 1m 30s
291:	learn: 1118254.4002887	total: 37.4s	remaining: 1m 30s
292:	learn: 1117683.6288604	total: 37.5s	remaining: 1m 30s
293:	learn: 1116897.8848170	total: 37.7s	remaining: 1m 30s
294:	learn: 1115955.0329072	total: 37.8s	remaining: 1m 30s
295:	learn: 1115364.1139382	total: 37.9s	remaining: 1m 30s
296:	learn: 1114483.6352071	total: 38.1s	remaining: 1m 30s
297:	learn: 1113900.4760025	total: 38.2s	remaining: 1m 29s
298:	learn: 1113368.2505448	total: 38.3s	remaining: 1m 29s
299:	learn: 1112612.7269338	total: 38.4s	remaining: 1m 29s
300:	learn: 1112091.3875404	total: 38.6s	remaining: 1m 29s

424:	learn: 1041924.7881701	total: 54.5s	remaining: 1m 13s
425:	learn: 1041498.7622799	total: 54.6s	remaining: 1m 13s
426:	learn: 1040935.9910273	total: 54.7s	remaining: 1m 13s
427:	learn: 1040591.9588529	total: 54.9s	remaining: 1m 13s
428:	learn: 1040357.2016605	total: 55s	remaining: 1m 13s
429:	learn: 1039882.1319410	total: 55.1s	remaining: 1m 13s
430:	learn: 1039180.3846827	total: 55.2s	remaining: 1m 12s
431:	learn: 1038605.3654187	total: 55.4s	remaining: 1m 12s
432:	learn: 1038019.9184706	total: 55.5s	remaining: 1m 12s
433:	learn: 1037408.2796448	total: 55.6s	remaining: 1m 12s
434:	learn: 1036801.0488776	total: 55.8s	remaining: 1m 12s
435:	learn: 1036474.3771543	total: 55.9s	remaining: 1m 12s
436:	learn: 1036102.6177762	total: 56s	remaining: 1m 12s
437:	learn: 1035662.0136206	total: 56.1s	remaining: 1m 12s
438:	learn: 1035231.1950859	total: 56.3s	remaining: 1m 11s
439:	learn: 1034774.0721247	total: 56.4s	remaining: 1m 11s
440:	learn: 1034362.7564918	total: 56.5s	remaining: 1m 11s
4

567:	learn: 981501.0494891	total: 1m 13s	remaining: 55.6s
568:	learn: 981106.6165900	total: 1m 13s	remaining: 55.5s
569:	learn: 980870.8963170	total: 1m 13s	remaining: 55.3s
570:	learn: 980443.0255542	total: 1m 13s	remaining: 55.2s
571:	learn: 980064.7133784	total: 1m 13s	remaining: 55.1s
572:	learn: 979647.8774415	total: 1m 13s	remaining: 55s
573:	learn: 979317.5017432	total: 1m 13s	remaining: 54.8s
574:	learn: 979052.1622179	total: 1m 14s	remaining: 54.7s
575:	learn: 978793.2711056	total: 1m 14s	remaining: 54.6s
576:	learn: 978317.8402168	total: 1m 14s	remaining: 54.4s
577:	learn: 977952.1340917	total: 1m 14s	remaining: 54.3s
578:	learn: 977467.5563529	total: 1m 14s	remaining: 54.2s
579:	learn: 977109.0810627	total: 1m 14s	remaining: 54.1s
580:	learn: 976831.0086969	total: 1m 14s	remaining: 53.9s
581:	learn: 976552.7422124	total: 1m 14s	remaining: 53.8s
582:	learn: 976092.0561132	total: 1m 15s	remaining: 53.7s
583:	learn: 975772.1326516	total: 1m 15s	remaining: 53.6s
584:	learn: 9753

709:	learn: 933657.4845890	total: 1m 31s	remaining: 37.3s
710:	learn: 933470.6637969	total: 1m 31s	remaining: 37.2s
711:	learn: 933166.0774284	total: 1m 31s	remaining: 37.1s
712:	learn: 932998.5298594	total: 1m 31s	remaining: 36.9s
713:	learn: 932622.6108457	total: 1m 31s	remaining: 36.8s
714:	learn: 932380.0540848	total: 1m 32s	remaining: 36.7s
715:	learn: 932123.4498147	total: 1m 32s	remaining: 36.5s
716:	learn: 931842.5172178	total: 1m 32s	remaining: 36.4s
717:	learn: 931508.1240590	total: 1m 32s	remaining: 36.3s
718:	learn: 931203.3272867	total: 1m 32s	remaining: 36.2s
719:	learn: 930993.8017793	total: 1m 32s	remaining: 36s
720:	learn: 930650.2829345	total: 1m 32s	remaining: 35.9s
721:	learn: 930373.1898703	total: 1m 32s	remaining: 35.8s
722:	learn: 930082.8117408	total: 1m 33s	remaining: 35.6s
723:	learn: 929927.2940730	total: 1m 33s	remaining: 35.5s
724:	learn: 929652.4424482	total: 1m 33s	remaining: 35.4s
725:	learn: 929295.3122165	total: 1m 33s	remaining: 35.3s
726:	learn: 9287

851:	learn: 895582.0516905	total: 1m 49s	remaining: 19.1s
852:	learn: 895477.7789593	total: 1m 49s	remaining: 19s
853:	learn: 895357.5440339	total: 1m 50s	remaining: 18.8s
854:	learn: 895171.5356034	total: 1m 50s	remaining: 18.7s
855:	learn: 895010.9748232	total: 1m 50s	remaining: 18.6s
856:	learn: 894674.9697226	total: 1m 50s	remaining: 18.4s
857:	learn: 894392.7411366	total: 1m 50s	remaining: 18.3s
858:	learn: 894188.7368037	total: 1m 50s	remaining: 18.2s
859:	learn: 894013.5028017	total: 1m 50s	remaining: 18s
860:	learn: 893714.1715563	total: 1m 51s	remaining: 17.9s
861:	learn: 893537.7772069	total: 1m 51s	remaining: 17.8s
862:	learn: 893277.4241842	total: 1m 51s	remaining: 17.7s
863:	learn: 892910.8204485	total: 1m 51s	remaining: 17.5s
864:	learn: 892707.2657511	total: 1m 51s	remaining: 17.4s
865:	learn: 892561.3198830	total: 1m 51s	remaining: 17.3s
866:	learn: 892401.5803872	total: 1m 51s	remaining: 17.1s
867:	learn: 892139.4515452	total: 1m 51s	remaining: 17s
868:	learn: 891943.7

995:	learn: 864679.1873435	total: 2m 8s	remaining: 516ms
996:	learn: 864577.6822117	total: 2m 8s	remaining: 387ms
997:	learn: 864249.4432383	total: 2m 8s	remaining: 258ms
998:	learn: 864030.7161472	total: 2m 8s	remaining: 129ms
999:	learn: 863855.2267835	total: 2m 9s	remaining: 0us


/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:588: FutureWarning: Series.base is deprecated and will be removed in a future version
  data.base is not None and isinstance(data, np.ndarray) \


[23:59:58] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


In [133]:
S_train, S_test, t_train, t_test = train_test_split( merged_train[features_columns], merged_train['naira_price'], test_size=0.3, random_state=42)


In [134]:
rf_model_partial = RandomForestRegressor().fit(S_train, t_train)

rf_pred = rf_model_partial.predict(S_test)
metric_score = mean_squared_error(t_test, rf_pred)
print("Metric Score: ", sqrt(metric_score) )

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


Metric Score:  1177574.0650444983


In [135]:
rf_pred = rf_model.predict(X_test)
metric_score = mean_squared_error(y_test, rf_pred)
print("Metric Score: ", sqrt(metric_score) )

Metric Score:  1559020.457815944


In [136]:
# Tuned XGB Boost;#max_depth=5, min_child_weight=2
xgb_model = xgb.XGBRegressor(max_depth=10).fit(S_train, t_train)
xgb_pred = xgb_model.predict(S_test)
metric_score = mean_squared_error(t_test, xgb_pred)
print("Metric Score: ", sqrt(metric_score) )

/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


[21:13:41] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
Metric Score:  1095500.2064441182


In [141]:
# For catboost with default iterations:

In [152]:
cat_model1000 = CatBoostRegressor(iterations = 1000).fit(S_train, t_train)

0:	learn: 3735122.9693122	total: 50.9ms	remaining: 50.8s
1:	learn: 3657748.9850691	total: 82.3ms	remaining: 41.1s
2:	learn: 3582752.3734193	total: 112ms	remaining: 37.2s
3:	learn: 3510575.0523653	total: 141ms	remaining: 35s
4:	learn: 3441160.0928018	total: 172ms	remaining: 34.2s
5:	learn: 3374568.4264227	total: 202ms	remaining: 33.5s
6:	learn: 3309355.1510659	total: 234ms	remaining: 33.1s
7:	learn: 3247106.9709383	total: 267ms	remaining: 33.1s
8:	learn: 3186633.3855642	total: 297ms	remaining: 32.7s
9:	learn: 3128546.4139547	total: 328ms	remaining: 32.5s
10:	learn: 3072655.9554309	total: 361ms	remaining: 32.5s
11:	learn: 3019408.5142197	total: 392ms	remaining: 32.3s
12:	learn: 2967649.5573769	total: 423ms	remaining: 32.1s
13:	learn: 2917668.7225517	total: 458ms	remaining: 32.3s
14:	learn: 2870092.6316164	total: 492ms	remaining: 32.3s
15:	learn: 2824041.7898204	total: 525ms	remaining: 32.3s
16:	learn: 2779929.6168111	total: 557ms	remaining: 32.2s
17:	learn: 2737575.9630144	total: 588ms	r

150:	learn: 1529958.1691418	total: 4.89s	remaining: 27.5s
151:	learn: 1528789.9596158	total: 4.92s	remaining: 27.5s
152:	learn: 1527041.2187728	total: 4.96s	remaining: 27.5s
153:	learn: 1525933.0466102	total: 4.99s	remaining: 27.4s
154:	learn: 1524540.4063778	total: 5.03s	remaining: 27.4s
155:	learn: 1523160.4376633	total: 5.06s	remaining: 27.4s
156:	learn: 1521066.4547392	total: 5.09s	remaining: 27.3s
157:	learn: 1520258.5274744	total: 5.12s	remaining: 27.3s
158:	learn: 1518033.0830513	total: 5.15s	remaining: 27.3s
159:	learn: 1516801.8744628	total: 5.18s	remaining: 27.2s
160:	learn: 1514602.3564223	total: 5.22s	remaining: 27.2s
161:	learn: 1513516.4169488	total: 5.25s	remaining: 27.2s
162:	learn: 1510634.9710626	total: 5.28s	remaining: 27.1s
163:	learn: 1508897.3030765	total: 5.32s	remaining: 27.1s
164:	learn: 1507427.2404017	total: 5.35s	remaining: 27.1s
165:	learn: 1506248.3649721	total: 5.38s	remaining: 27.1s
166:	learn: 1504763.5649411	total: 5.42s	remaining: 27s
167:	learn: 1503

299:	learn: 1384460.1106602	total: 9.77s	remaining: 22.8s
300:	learn: 1383912.3291471	total: 9.81s	remaining: 22.8s
301:	learn: 1383138.2551485	total: 9.84s	remaining: 22.7s
302:	learn: 1382714.9154131	total: 9.87s	remaining: 22.7s
303:	learn: 1382255.3276535	total: 9.9s	remaining: 22.7s
304:	learn: 1381568.3940213	total: 9.94s	remaining: 22.6s
305:	learn: 1380778.7930469	total: 9.97s	remaining: 22.6s
306:	learn: 1380060.6476294	total: 10s	remaining: 22.6s
307:	learn: 1379205.3577435	total: 10s	remaining: 22.5s
308:	learn: 1378726.8021256	total: 10.1s	remaining: 22.5s
309:	learn: 1377664.6459174	total: 10.1s	remaining: 22.5s
310:	learn: 1377109.3376768	total: 10.1s	remaining: 22.4s
311:	learn: 1376625.6782661	total: 10.2s	remaining: 22.4s
312:	learn: 1375946.3857819	total: 10.2s	remaining: 22.4s
313:	learn: 1375471.5377709	total: 10.2s	remaining: 22.3s
314:	learn: 1375187.4664803	total: 10.3s	remaining: 22.3s
315:	learn: 1374782.1153631	total: 10.3s	remaining: 22.3s
316:	learn: 1374117

447:	learn: 1310782.7993806	total: 14.6s	remaining: 18s
448:	learn: 1310241.9192960	total: 14.7s	remaining: 18s
449:	learn: 1309499.9302956	total: 14.7s	remaining: 18s
450:	learn: 1309285.1648272	total: 14.7s	remaining: 17.9s
451:	learn: 1309055.4533964	total: 14.8s	remaining: 17.9s
452:	learn: 1308714.4677225	total: 14.8s	remaining: 17.9s
453:	learn: 1308266.4512261	total: 14.8s	remaining: 17.8s
454:	learn: 1307883.5800409	total: 14.9s	remaining: 17.8s
455:	learn: 1307473.5503760	total: 14.9s	remaining: 17.8s
456:	learn: 1307241.5291514	total: 14.9s	remaining: 17.7s
457:	learn: 1306991.3139794	total: 15s	remaining: 17.7s
458:	learn: 1306854.3104996	total: 15s	remaining: 17.7s
459:	learn: 1306397.5005224	total: 15s	remaining: 17.6s
460:	learn: 1305964.0866432	total: 15.1s	remaining: 17.6s
461:	learn: 1305461.4095354	total: 15.1s	remaining: 17.6s
462:	learn: 1305078.9492756	total: 15.1s	remaining: 17.6s
463:	learn: 1304419.0024504	total: 15.2s	remaining: 17.5s
464:	learn: 1304076.495109

591:	learn: 1263690.1179300	total: 19.4s	remaining: 13.3s
592:	learn: 1263441.5312353	total: 19.4s	remaining: 13.3s
593:	learn: 1263192.0800482	total: 19.4s	remaining: 13.3s
594:	learn: 1262898.1495375	total: 19.5s	remaining: 13.2s
595:	learn: 1262631.8112021	total: 19.5s	remaining: 13.2s
596:	learn: 1262373.0884349	total: 19.5s	remaining: 13.2s
597:	learn: 1262218.2461916	total: 19.6s	remaining: 13.1s
598:	learn: 1261985.6348656	total: 19.6s	remaining: 13.1s
599:	learn: 1261770.7643681	total: 19.6s	remaining: 13.1s
600:	learn: 1261417.3430485	total: 19.7s	remaining: 13s
601:	learn: 1261127.0003618	total: 19.7s	remaining: 13s
602:	learn: 1260907.2113070	total: 19.7s	remaining: 13s
603:	learn: 1260730.7624131	total: 19.8s	remaining: 13s
604:	learn: 1260553.9314170	total: 19.8s	remaining: 12.9s
605:	learn: 1260242.0177137	total: 19.8s	remaining: 12.9s
606:	learn: 1259925.7480630	total: 19.9s	remaining: 12.9s
607:	learn: 1259691.1251128	total: 19.9s	remaining: 12.8s
608:	learn: 1259534.49

739:	learn: 1227390.1484224	total: 24.2s	remaining: 8.5s
740:	learn: 1227306.5227041	total: 24.2s	remaining: 8.46s
741:	learn: 1227115.1800917	total: 24.3s	remaining: 8.43s
742:	learn: 1226973.2789849	total: 24.3s	remaining: 8.4s
743:	learn: 1226802.1775905	total: 24.3s	remaining: 8.37s
744:	learn: 1226750.9988703	total: 24.3s	remaining: 8.33s
745:	learn: 1226582.5904084	total: 24.4s	remaining: 8.3s
746:	learn: 1226362.5495047	total: 24.4s	remaining: 8.27s
747:	learn: 1226118.0990401	total: 24.4s	remaining: 8.23s
748:	learn: 1225922.8402463	total: 24.5s	remaining: 8.2s
749:	learn: 1225817.2533748	total: 24.5s	remaining: 8.17s
750:	learn: 1225680.3073542	total: 24.5s	remaining: 8.14s
751:	learn: 1225601.5412740	total: 24.6s	remaining: 8.1s
752:	learn: 1225350.3831350	total: 24.6s	remaining: 8.07s
753:	learn: 1225010.7483249	total: 24.6s	remaining: 8.04s
754:	learn: 1224897.1283289	total: 24.7s	remaining: 8.01s
755:	learn: 1224578.6910742	total: 24.7s	remaining: 7.97s
756:	learn: 1224195

884:	learn: 1199524.6240476	total: 28.9s	remaining: 3.75s
885:	learn: 1199223.2366518	total: 28.9s	remaining: 3.72s
886:	learn: 1198928.8843867	total: 28.9s	remaining: 3.69s
887:	learn: 1198711.4722226	total: 29s	remaining: 3.65s
888:	learn: 1198623.2051538	total: 29s	remaining: 3.62s
889:	learn: 1198412.1975952	total: 29s	remaining: 3.59s
890:	learn: 1198289.4735891	total: 29.1s	remaining: 3.55s
891:	learn: 1198057.9146980	total: 29.1s	remaining: 3.52s
892:	learn: 1197879.9248200	total: 29.1s	remaining: 3.49s
893:	learn: 1197739.1439127	total: 29.2s	remaining: 3.46s
894:	learn: 1197610.7971499	total: 29.2s	remaining: 3.42s
895:	learn: 1197481.6169737	total: 29.2s	remaining: 3.39s
896:	learn: 1197370.3871224	total: 29.3s	remaining: 3.36s
897:	learn: 1197260.0585086	total: 29.3s	remaining: 3.33s
898:	learn: 1197049.3394960	total: 29.3s	remaining: 3.29s
899:	learn: 1196958.6178488	total: 29.4s	remaining: 3.26s
900:	learn: 1196837.8622840	total: 29.4s	remaining: 3.23s
901:	learn: 1196501.

In [153]:
cat_pred = cat_model1000.predict(S_test)
metric_score = mean_squared_error(t_test, cat_pred)
print("Metric Score(t_test): ", sqrt(metric_score) )
print(" ")
cat_pred = cat_model1000.predict(X_test)
metric_score = mean_squared_error(y_test, cat_pred)
print("Metric Score(y_test): ", sqrt(metric_score) )

Metric Score(t_test):  1293109.9786918387
 
Metric Score(y_test):  1223014.3285901137


In [146]:
cat1000 = CatBoostRegressor(iterations = 1000).fit(merged_train[features_columns], merged_train["naira_price"])


0:	learn: 3743322.6570507	total: 76.5ms	remaining: 1m 16s
1:	learn: 3665882.5846503	total: 121ms	remaining: 1m
2:	learn: 3590822.8612556	total: 165ms	remaining: 54.9s
3:	learn: 3518212.4114884	total: 213ms	remaining: 53.1s
4:	learn: 3448631.7585502	total: 258ms	remaining: 51.4s
5:	learn: 3380942.0208656	total: 309ms	remaining: 51.1s
6:	learn: 3316989.2655217	total: 358ms	remaining: 50.8s
7:	learn: 3255192.1998854	total: 406ms	remaining: 50.3s
8:	learn: 3194582.1658353	total: 455ms	remaining: 50.1s
9:	learn: 3137284.5245079	total: 500ms	remaining: 49.5s
10:	learn: 3081694.5743624	total: 547ms	remaining: 49.2s
11:	learn: 3028747.8016331	total: 596ms	remaining: 49.1s
12:	learn: 2977328.2228099	total: 646ms	remaining: 49.1s
13:	learn: 2927628.3238375	total: 693ms	remaining: 48.8s
14:	learn: 2880121.3368142	total: 739ms	remaining: 48.5s
15:	learn: 2833914.1239887	total: 786ms	remaining: 48.3s
16:	learn: 2790049.0587582	total: 834ms	remaining: 48.2s
17:	learn: 2747476.9023109	total: 882ms	re

148:	learn: 1533130.7553077	total: 7.11s	remaining: 40.6s
149:	learn: 1531565.0468421	total: 7.16s	remaining: 40.6s
150:	learn: 1528518.6526560	total: 7.2s	remaining: 40.5s
151:	learn: 1527293.6418595	total: 7.25s	remaining: 40.4s
152:	learn: 1525543.2935575	total: 7.3s	remaining: 40.4s
153:	learn: 1524620.1363441	total: 7.34s	remaining: 40.3s
154:	learn: 1522078.8287727	total: 7.39s	remaining: 40.3s
155:	learn: 1520541.9301186	total: 7.44s	remaining: 40.2s
156:	learn: 1519160.3085265	total: 7.49s	remaining: 40.2s
157:	learn: 1518061.6219572	total: 7.53s	remaining: 40.1s
158:	learn: 1516808.5304916	total: 7.58s	remaining: 40.1s
159:	learn: 1515326.2201519	total: 7.63s	remaining: 40s
160:	learn: 1513906.9847899	total: 7.67s	remaining: 40s
161:	learn: 1512936.5342798	total: 7.72s	remaining: 39.9s
162:	learn: 1511861.4678910	total: 7.76s	remaining: 39.9s
163:	learn: 1510929.6597350	total: 7.81s	remaining: 39.8s
164:	learn: 1509382.2184171	total: 7.85s	remaining: 39.8s
165:	learn: 1508433.

293:	learn: 1396543.3608245	total: 13.8s	remaining: 33.2s
294:	learn: 1395455.9081642	total: 13.9s	remaining: 33.1s
295:	learn: 1394667.9639917	total: 13.9s	remaining: 33.1s
296:	learn: 1394411.2774579	total: 13.9s	remaining: 33s
297:	learn: 1393903.0090981	total: 14s	remaining: 33s
298:	learn: 1392858.1751778	total: 14s	remaining: 32.9s
299:	learn: 1392552.4990992	total: 14.1s	remaining: 32.9s
300:	learn: 1391851.0060646	total: 14.1s	remaining: 32.8s
301:	learn: 1391247.3003555	total: 14.2s	remaining: 32.8s
302:	learn: 1390204.5702787	total: 14.2s	remaining: 32.7s
303:	learn: 1389637.7052534	total: 14.3s	remaining: 32.7s
304:	learn: 1388612.5079372	total: 14.3s	remaining: 32.6s
305:	learn: 1387780.3577327	total: 14.4s	remaining: 32.6s
306:	learn: 1387428.6476835	total: 14.4s	remaining: 32.6s
307:	learn: 1386802.9548378	total: 14.5s	remaining: 32.5s
308:	learn: 1385634.8555069	total: 14.5s	remaining: 32.5s
309:	learn: 1385233.7059071	total: 14.6s	remaining: 32.4s
310:	learn: 1383686.21

438:	learn: 1323153.8426809	total: 20.5s	remaining: 26.2s
439:	learn: 1322512.2982829	total: 20.5s	remaining: 26.1s
440:	learn: 1322123.3818531	total: 20.6s	remaining: 26.1s
441:	learn: 1321756.9105791	total: 20.6s	remaining: 26s
442:	learn: 1321333.2659868	total: 20.7s	remaining: 26s
443:	learn: 1320934.0774100	total: 20.7s	remaining: 26s
444:	learn: 1320533.1878362	total: 20.8s	remaining: 25.9s
445:	learn: 1320117.1103778	total: 20.8s	remaining: 25.9s
446:	learn: 1319865.2095261	total: 20.9s	remaining: 25.8s
447:	learn: 1319408.0026040	total: 20.9s	remaining: 25.8s
448:	learn: 1319035.3686758	total: 21s	remaining: 25.7s
449:	learn: 1318837.7937170	total: 21s	remaining: 25.7s
450:	learn: 1318500.7148052	total: 21s	remaining: 25.6s
451:	learn: 1318156.4299210	total: 21.1s	remaining: 25.6s
452:	learn: 1317867.7362817	total: 21.1s	remaining: 25.5s
453:	learn: 1317492.4276266	total: 21.2s	remaining: 25.5s
454:	learn: 1317183.5130119	total: 21.2s	remaining: 25.4s
455:	learn: 1316985.090231

583:	learn: 1276467.4722630	total: 27.2s	remaining: 19.4s
584:	learn: 1276307.3032027	total: 27.2s	remaining: 19.3s
585:	learn: 1275851.8836535	total: 27.3s	remaining: 19.3s
586:	learn: 1275667.0421815	total: 27.3s	remaining: 19.2s
587:	learn: 1275433.3783329	total: 27.4s	remaining: 19.2s
588:	learn: 1275159.8537088	total: 27.4s	remaining: 19.1s
589:	learn: 1274959.0018690	total: 27.5s	remaining: 19.1s
590:	learn: 1274709.9685704	total: 27.5s	remaining: 19s
591:	learn: 1274434.1256831	total: 27.6s	remaining: 19s
592:	learn: 1274174.6952049	total: 27.6s	remaining: 19s
593:	learn: 1274027.0431831	total: 27.7s	remaining: 18.9s
594:	learn: 1273779.4265321	total: 27.7s	remaining: 18.9s
595:	learn: 1273602.7583899	total: 27.7s	remaining: 18.8s
596:	learn: 1273428.6525995	total: 27.8s	remaining: 18.8s
597:	learn: 1273342.4493668	total: 27.8s	remaining: 18.7s
598:	learn: 1273060.9369656	total: 27.9s	remaining: 18.7s
599:	learn: 1272790.9730964	total: 27.9s	remaining: 18.6s
600:	learn: 1272661.

728:	learn: 1242664.4975953	total: 33.8s	remaining: 12.6s
729:	learn: 1242350.4108485	total: 33.9s	remaining: 12.5s
730:	learn: 1242211.5950574	total: 33.9s	remaining: 12.5s
731:	learn: 1241916.8142678	total: 34s	remaining: 12.4s
732:	learn: 1241736.7352317	total: 34s	remaining: 12.4s
733:	learn: 1241611.7370781	total: 34.1s	remaining: 12.3s
734:	learn: 1241460.6033147	total: 34.1s	remaining: 12.3s
735:	learn: 1241209.6711643	total: 34.1s	remaining: 12.2s
736:	learn: 1241041.4421603	total: 34.2s	remaining: 12.2s
737:	learn: 1240901.5931304	total: 34.2s	remaining: 12.2s
738:	learn: 1240715.4675565	total: 34.3s	remaining: 12.1s
739:	learn: 1240556.9498828	total: 34.3s	remaining: 12.1s
740:	learn: 1240366.9578709	total: 34.4s	remaining: 12s
741:	learn: 1240238.5948730	total: 34.4s	remaining: 12s
742:	learn: 1239930.1430039	total: 34.5s	remaining: 11.9s
743:	learn: 1239883.2496722	total: 34.5s	remaining: 11.9s
744:	learn: 1239665.3071300	total: 34.5s	remaining: 11.8s
745:	learn: 1239391.65

873:	learn: 1214988.4502911	total: 40.4s	remaining: 5.83s
874:	learn: 1214841.0620255	total: 40.5s	remaining: 5.78s
875:	learn: 1214750.2889524	total: 40.5s	remaining: 5.74s
876:	learn: 1214631.1322083	total: 40.6s	remaining: 5.69s
877:	learn: 1214441.2071935	total: 40.6s	remaining: 5.64s
878:	learn: 1214308.5748469	total: 40.7s	remaining: 5.6s
879:	learn: 1214144.3987436	total: 40.7s	remaining: 5.55s
880:	learn: 1214007.2862027	total: 40.8s	remaining: 5.5s
881:	learn: 1213834.7219128	total: 40.8s	remaining: 5.46s
882:	learn: 1213770.8351625	total: 40.8s	remaining: 5.41s
883:	learn: 1213639.4932776	total: 40.9s	remaining: 5.36s
884:	learn: 1213368.6380677	total: 40.9s	remaining: 5.32s
885:	learn: 1213308.3561636	total: 41s	remaining: 5.27s
886:	learn: 1213229.0384924	total: 41s	remaining: 5.22s
887:	learn: 1213145.2742411	total: 41.1s	remaining: 5.18s
888:	learn: 1213072.6670997	total: 41.1s	remaining: 5.13s
889:	learn: 1212990.5869819	total: 41.1s	remaining: 5.08s
890:	learn: 1212761.

In [142]:
xgb_model = xgb.XGBRegressor(max_depth=10).fit(merged_train[features_columns], merged_train["naira_price"])


/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:588: FutureWarning: Series.base is deprecated and will be removed in a future version
  data.base is not None and isinstance(data, np.ndarray) \


[21:25:41] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


In [144]:
4+3

7

In [175]:
test_predictions = cat_model1000.predict(test_copy[features_columns])

test_submission = pd.DataFrame({"id" : zero_test["ID"], "naira_price" : np.round(test_predictions, decimals=1)})

test_submission.to_csv("dsn-car-price-cat-tuned.csv", index=False)

In [145]:
test_predictions = xgb_model.predict(test_copy[features_columns])

test_submission = pd.DataFrame({"id" : zero_test["ID"], "naira_price" : np.round(test_predictions, decimals=1)})

test_submission.to_csv("dsn-car-price-xgb-full-COMBINED.csv", index=False)

In [86]:
test_submission.head()

id  naira_price
0   2    2503897.9
1   6    1569589.0
2   7    6063041.6
3  11     454777.1
4  12    1163392.7

9

In [115]:
#Using Tuned xgb on full dataset:
xgb_model = xgb.XGBRegressor(max_depth=10).fit(train_copy[features_columns], train_copy["naira_price"])


/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \
/mnt/disks/user/anaconda3/lib/python3.6/site-packages/xgboost/core.py:588: FutureWarning: Series.base is deprecated and will be removed in a future version
  data.base is not None and isinstance(data, np.ndarray) \


[20:50:08] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


In [ ]:
rf_model = RandomForestRegressor().fit(train_copy[features_columns], train_copy["naira_price"])
